In [1]:
# Import standard libraries
import os
import sys
import importlib
import datetime as dt
import time
from pathlib import Path
from contextlib import redirect_stdout

# Import data manipulation libraries
import numpy as np
import pandas as pd

# Import visualization libraries
import matplotlib.pyplot as plt
import seaborn as sns

In [2]:
# Import custom modules - NEED WINDOWS OS
#from CoEQWAL.imports import AuxFunctions as af, cs3, csPlots, cs_util as util, dss3_functions_reference as dss
# import AuxFunctions as af, cs3, csPlots, cs_util as util, dss3_functions_reference as dss

## Define file names and ranges for DSS and vars

In [3]:
# list of study names file, tab, range, and extension
DssList = r'../dss_may_2024/Exploratory_Results_v03/callite_expl03_run_listing.xlsx'
DssTab = 'callite_expl03_run_listing'
DssMin = 'A1'
DssMax = 'A601'
DssExt = '_DV.dss'
DssOut = 'dss_names.csv'

# list of relevant variables file, tab, and range (B & C parts)
VarList = r'../Selected Studies and Variables/may27_variables.xlsx'
VarTab = 'May EDA'
VarMin = 'B1'
VarMax = 'C51'
VarOut = 'EDA_vars_07_01_24.csv'

# launch file path to (or CalSim) studies and output csv name
StudyDir = r'../dss_may_2024/Exploratory_Results_v03'
SourceDataDir = r'../output/convert/'
DataDir = r'../data/metrics/'
DataOut = 'convert_EDA_data_07_01_24.csv'
WetDataOut = 'convert_wet_EDA_data_07_01_24.csv'
DryDataOut = 'convert_dry_EDA_data_07_01_24.csv'

# WY csv
WYcsv = 'wytypestable.csv'

# Metrics file
MetricsOut = 'metrics_07_01_2024.csv'
WetMetricsOut = 'wet_metrics_07_01_2024.csv'
DryMetricsOut = 'dry_metrics_07_01_2024.csv'

MetricsSdOut = 'sd_metrics_07_01_2024.csv'
WetMetricsSdOut = 'sd_wet_metrics_07_01_2024.csv'
DryMetricsSdOut = 'sd_dry_metrics_07_01_2024.csv'

# visualization path
fPath = "../output/metrics"

### Specify Variable List for Metrics

In [294]:
metrics_output = ["Apr_Avg_NODstorage_TAF", "Sep_Avg_NODstorage_TAF" ,"Ann_Avg_CVPSWPTotDel_TAF", 
                  "Ann_Avg_BanksJones_TAF", "Ann_Avg_NDO_TAF", "Fall_Avg_X2_KM", "Spring_Avg_X2_KM"]

metrics_sd_output = ["Std_Apr_Avg_NODstorage_TAF", "Std_Sep_Avg_NODstorage_TAF" ,"Std_Ann_Avg_CVPSWPTotDel_TAF",
                  "Std_Ann_Avg_BanksJones_TAF", "Std_Ann_Avg_NDO_TAF", "Std_Fall_Avg_X2_KM", "Std_Spring_Avg_X2_KM"]

wet_metrics_output = ["Wet_Apr_Avg_NODstorage_TAF", "Wet_Sep_Avg_NODstorage_TAF" ,"Wet_Ann_Avg_CVPSWPTotDel_TAF",
                                       "Wet_Ann_Avg_BanksJones_TAF", "Wet_Ann_Avg_NDO_TAF", "Wet_Fall_Avg_X2_KM", "Wet_Spring_Avg_X2_KM"]

wet_metrics_sd_output = ["Wet_Std_Apr_Avg_NODstorage_TAF", "Wet_Std_Sep_Avg_NODstorage_TAF" ,"Wet_Std_Ann_Avg_CVPSWPTotDel_TAF",
                      "Wet_Std_Ann_Avg_BanksJones_TAF", "Wet_Std_Ann_Avg_NDO_TAF", "Wet_Std_Fall_Avg_X2_KM", "Wet_Std_Spring_Avg_X2_KM"]

dry_metrics_output = ["Dry_Apr_Avg_NODstorage_TAF", "Dry_Sep_Avg_NODstorage_TAF" ,"Dry_Ann_Avg_CVPSWPTotDel_TAF",
                     "Dry_Ann_Avg_BanksJones_TAF", "Dry_Ann_Avg_NDO_TAF", "Dry_Fall_Avg_X2_KM", "Dry_Spring_Avg_X2_KM"]

dry_metrics_sd_output = ["Dry_Std_Apr_Avg_NODstorage_TAF", "Dry_Std_Sep_Avg_NODstorage_TAF" ,"Dry_Std_Ann_Avg_CVPSWPTotDel_TAF",
                      "Dry_Std_Ann_Avg_BanksJones_TAF", "Dry_Std_Ann_Avg_NDO_TAF", "Dry_Std_Fall_Avg_X2_KM", "Dry_Std_Spring_Avg_X2_KM"]

### Read Data

In [5]:
df = pd.read_csv(os.path.join(SourceDataDir, DataOut), header=[0, 1, 2, 3, 4, 5, 6], index_col=0, parse_dates=True)
df = df.loc[:, ~df.columns.get_level_values(6).str.contains('CFS.1')]
wet_df = pd.read_csv(os.path.join(SourceDataDir, WetDataOut), header=[0, 1, 2, 3, 4, 5, 6], index_col=0, parse_dates=True)
wet_df = wet_df.loc[:, ~wet_df.columns.get_level_values(6).str.contains('CFS.1')].iloc[:, :-2]
dry_df = pd.read_csv(os.path.join(SourceDataDir, DryDataOut), header=[0, 1, 2, 3, 4, 5, 6], index_col=0, parse_dates=True)
dry_df = dry_df.loc[:, ~dry_df.columns.get_level_values(6).str.contains('CFS.1')].iloc[:, :-2]
dss_names = pd.read_csv(os.path.join(DataDir, DssOut))["0"].tolist()
# df.head(5)
#var_list = var_df["DSS Part B"].tolist()

##### REMAP DRY & WET_DF - to be moved into Extract notebook later

In [6]:
def add_water_year_column(df):
    df['Date'] = pd.to_datetime(df.index)
    df['Year'] = df['Date'].dt.year
    df['Month'] = df['Date'].dt.month
    df['WaterYear'] = np.where(df['Month'] >= 10, df['Year'] + 1, df['Year'])
    return df.drop(["Date", "Year", "Month"], axis = 1)

In [7]:
# df = add_water_year_column(df)
# df

In [8]:
# wy_value_map = {
#     1: "Wet",
#     2: "Wet",
#     3: "Wet",
#     4: "Dry",
#     5: "Dry",
# }

In [9]:
# df_wy = pd.read_csv(DataDir + "wytypestable.csv")
# df_wy = df_wy[["SACindex_0", "WATERYEAR"]]
# df_wy

In [10]:
# year_to_category = df_wy.set_index('WATERYEAR')['SACindex_0'].map(wy_value_map).to_dict()
# df['Category'] = df['WaterYear'].map(year_to_category)
# 
# wet_df = df[df['Category'] == "Wet"]
# dry_df = df[df['Category'] == "Dry"]
# 
# df.drop(columns=['Category'], inplace=True)
# wet_df.drop(columns=['Category'], inplace=True)
# dry_df.drop(columns=['Category'], inplace=True)

## Subset by variable across studies

In [11]:
def create_subset_var(df, varname):
    """ 
    Filters df to return columns that contain the string varname
    :param df: Dataframe to filter
    :param varname: variable of interest, e.g. S_SHSTA
    """
    filtered_columns = df.columns.get_level_values(1).str.contains(varname)
    return df.loc[:, filtered_columns]

In [12]:
def create_subset_unit(df, varname, units):
    """ 
    Filters df to return columns that contain the string varname and units
    :param df: Dataframe to filter
    :param varname: variable of interest, e.g. S_SHSTA
    :param units: units of interest
    """
    var_filter = df.columns.get_level_values(1).str.contains(varname)
    unit_filter = df.columns.get_level_values(6).str.contains(units)
    filtered_columns = var_filter & unit_filter
    return df.loc[:, filtered_columns]

In [13]:
def create_subset_list(df, var_names):
    """ 
    Filters df to return columns that contain any of the strings in var_names.
    :param df: Dataframe to filter.
    :param var_names: List of variables of interest, e.g. ['S_SHSTA', 'S_OROVL'].
    """
    filtered_columns = df.columns.get_level_values(1).str.contains('|'.join(var_names))
    return df.loc[:, filtered_columns]

In [14]:
def compute_annual_means(df, var, study_lst, units, months):
    subset_df = create_subset_unit(df, var, units).iloc[:, study_lst]
    subset_df = add_water_year_column(subset_df)
    
    if months is not None:
        subset_df = subset_df[subset_df.index.month.isin(months)]
        
    annual_sum = subset_df.groupby('WaterYear').sum()

    return annual_sum

In [15]:
def compute_mean(df, variable_list, study_lst, units, months = None):
    df = compute_annual_means(df, variable_list, study_lst, units, months)
    num_years = len(df)
    return (df.sum() / num_years).iloc[-1]

In [16]:
def compute_sd(df, variable_list, units, varname, months = None):
    subset_df = create_subset_unit(df, variable_list, units)
    if months is not None:
        subset_df = subset_df[subset_df.index.month.isin(months)]
    
    standard_deviation = subset_df.std().to_frame(name=varname).reset_index(drop=True)
    return standard_deviation

# Base Functions

In [17]:
def count_exceedances_for_thresholds(exceedance_probs):
    thresholds = np.arange(0.1, 1.0, 0.05)
    exceedance_counts = pd.DataFrame(index=thresholds, columns=exceedance_probs.columns)

    for thresh in thresholds:
        for col in exceedance_probs.columns:
            exceedance_counts.loc[thresh, col] = (exceedance_probs[col] > thresh).sum()

    return exceedance_counts

In [18]:
def count_exceedance_days(data, threshold):
    exceedance_counts = pd.DataFrame(np.nan, index=[0], columns=data.columns)

    for col in data.columns:
        exceedance_counts.loc[0, col] = (data[col] > threshold).sum()
    return exceedance_counts

In [19]:
def calculate_monthly_average(flow_data):
    flow_data = flow_data.reset_index()
    flow_data['Date'] = pd.to_datetime(flow_data.iloc[:, 0])

    flow_data.loc[:, 'Month'] = flow_data['Date'].dt.strftime('%m')
    flow_data.loc[:, 'Year'] = flow_data['Date'].dt.strftime('%Y')

    flow_values = flow_data.iloc[:, 1:]
    monthly_avg = flow_values.groupby(flow_data['Month']).mean().reset_index()

    monthly_avg.rename(columns={'Month': 'Month'}, inplace=True)
    return monthly_avg

In [20]:
def calculate_flow_sum_per_year(flow_data):
    flow_data = add_water_year_column(flow_data)
    flow_sum_per_year = flow_data.groupby('WaterYear').sum(numeric_only=True).reset_index()

    return flow_sum_per_year

## Plotting Functions

Need to look example file "general_plots_v20231115.py" is posted to the Google Drive with the example files/scripts in the Python_DSS directory (here: https://drive.google.com/drive/folders/1JbN0eYKNM0772P0XMj0S7Fyl7I9GZxfW?usp=drive_link). Also the plotting.yml file to list out and define which CalSim/CalLite studies to plot and analyze. If you want to test it out yourself, you'll need ot update the paths to your own CalLite/CalSim studies.


In [21]:
def plot_ts(df, pTitle = 'Time Series', xLab = 'Date', lTitle = 'Studies', fTitle = 'mon_tot', pSave = True, fPath = fPath):
    """
    Plots a time-series graph for a given MultiIndex dataframe (follows calsim conventions)
    
    The function assumes the DataFrame columns follow a specific naming
    convention where the last part of the name indicates the study.
    """
    
    var = '_'.join(df.columns[0][1].split('_')[:-1])
    colormap = plt.cm.tab20
    colors = [colormap(i) for i in range(df.shape[1])]
    colors[-1] = [0,0,0,1]

    count = 0
    
    plt.figure(figsize=(14, 8))
    
    default_font_size = plt.rcParams['font.size']
    scaled_font_size = 1.5 * default_font_size # Change it to font size you want
    default_line_width = plt.rcParams['lines.linewidth']  
    scaled_line_width = 1.5 * default_line_width
    
    studies = [col[1].split('_')[-1] for col in df.columns]

    for study in studies:
        study_cols = [col for col in df.columns if col[1].endswith(study)]
        for col in study_cols:
            sns.lineplot(data=df, x=df.index, y=col, label=f'{study}', color = colors[count], linewidth=scaled_line_width)
            count+=1
            
    plt.title(var + ' ' + pTitle, fontsize=scaled_font_size*2)
    plt.xlabel(xLab, fontsize=scaled_font_size*1.5)
    plt.ylabel(var+"\nUnits: " + df.columns[0][6], fontsize=scaled_font_size*1.5)

    plt.legend(title=lTitle, title_fontsize = scaled_font_size*1.5, fontsize=scaled_font_size*1.25, bbox_to_anchor=(1.02, 1), loc='upper left', borderaxespad=0)
    plt.xticks(rotation=45, fontsize=scaled_font_size)  
    plt.yticks(fontsize=scaled_font_size)  
    plt.tight_layout()  
     
    if pSave:
        plt.savefig(f'{fPath}/visualizations/{var}_{fTitle}.png', format = 'png', bbox_inches='tight', dpi=600, transparent=False)
        
    plt.show()
   

In [22]:
def plot_annual_totals(df, xLab = 'Date', pTitle = 'Annual Totals', lTitle = 'Studies', fTitle = 'ann_tot', pSave = True, fPath = fPath):
    """
    Plots a time-series graph of annual totals for a given MultiIndex Dataframe that 
    follows calsim conventions
    
    The function assumes the DataFrame columns follow a specific naming
    convention where the last part of the name indicates the study. 
    """
    
    annualized_df = pd.DataFrame()
    var = '_'.join(df.columns[0][1].split('_')[:-1])
    studies = [col[1].split('_')[-1] for col in df.columns]
        
    colormap = plt.cm.tab20
    colors = [colormap(i) for i in range(df.shape[1])]
    colors[-1] = [0,0,0,1]
        
    i=0

    plt.figure(figsize=(14, 8))
        
    default_font_size = plt.rcParams['font.size']
    scaled_font_size = 1.5 * default_font_size # Change it to font size you want
    default_line_width = plt.rcParams['lines.linewidth']  
    scaled_line_width = 1.5 * default_line_width
    
    for study in studies:
        study_cols = [col for col in df.columns if col[1].endswith(study)]
        for col in study_cols:
            with redirect_stdout(open(os.devnull, 'w')):
                df_ann = csPlots.annualize(df.loc[:, [df.columns[i]]])
                annualized_df = pd.concat([annualized_df, df_ann], axis=1)
                annualized_col_name = df_ann.columns[0]
                sns.lineplot(data = df_ann, x=df_ann.index, y=annualized_col_name, label=f'{study}', color = colors[i],
                            linewidth = scaled_line_width)
                i+=1
                    

    plt.title(var + ' ' + pTitle, fontsize=scaled_font_size*2)
    plt.xlabel(xLab, fontsize=scaled_font_size*1.5)
    plt.ylabel(var+"\nUnits: " + df.columns[0][6], fontsize=scaled_font_size*1.5)

    plt.legend(title=lTitle, title_fontsize = scaled_font_size*1.5, fontsize=scaled_font_size*1.25, bbox_to_anchor=(1.02, 1), loc='upper left', borderaxespad=0)
    plt.xticks(rotation=45, fontsize=scaled_font_size)  
    plt.yticks(fontsize=scaled_font_size)  
    plt.tight_layout()  
        
    if pSave:
        plt.savefig(f'{fPath}/visualizations/{var}_{fTitle}.png', format = 'png', bbox_inches='tight', dpi=600, transparent=False)
        
    plt.show()
    return annualized_df 

In [23]:
def plot_exceedance(df, month = "All Months", xLab = 'Probability', pTitle = 'Exceedance Probability', lTitle = 'Studies', fTitle = 'exceed', pSave = True, fPath = fPath):
    """
    Plots an exceedance graph for a given MultiIndex Dataframe that follows calsim conventions
  
    The function assumes the DataFrame columns follow a specific naming
    convention where the last part of the name indicates the study. 
    """
    pTitle = pTitle + " " + month
    fTitle = fTitle + " " + month
    
    var = '_'.join(df.columns[0][1].split('_')[:-1])
    studies = [col[1].split('_')[-1] for col in df.columns]
    i=0
    
    colormap = plt.cm.tab20
    colors = [colormap(i) for i in range(df.shape[1])]
    colors[-1] = [0,0,0,1]

    plt.figure(figsize=(14, 8))
            
    default_font_size = plt.rcParams['font.size']
    scaled_font_size = 1.5 * default_font_size # Change it to font size you want
    default_line_width = plt.rcParams['lines.linewidth']  
    scaled_line_width = 1.5 * default_line_width

    for study in studies:
        study_cols = [col for col in df.columns if col[1].endswith(study)]
        for col in study_cols:
            df_ex = csPlots.single_exceed(df, df.columns[i])
            ex_col_name = df_ex.columns[0]
            sns.lineplot(data = df_ex, x=df_ex.index, y=ex_col_name, label=f'{study}', color = colors[i], linewidth = scaled_line_width)
            i+=1

    plt.title(var + ' ' + pTitle, fontsize=scaled_font_size*2)
    plt.xlabel(xLab, fontsize=scaled_font_size*1.5)
    plt.ylabel(var+"\nUnits: " + df.columns[0][6], fontsize=scaled_font_size*1.5)
    plt.legend(title=lTitle, title_fontsize = scaled_font_size*1.5, fontsize=scaled_font_size*1.25, bbox_to_anchor=(1.02, 1), loc='upper left', borderaxespad=0)
    plt.xticks(rotation=45, fontsize=scaled_font_size)  
    plt.yticks(fontsize=scaled_font_size)  
    plt.tight_layout()  
    
    if pSave:
        plt.savefig(f'{fPath}/visualizations/{var}_{fTitle}.png', format = 'png', bbox_inches='tight', dpi=600, transparent=False)
        
    plt.show()

In [24]:
def plot_moy_averages(df, xLab = 'Month of Year', pTitle = 'Month of Year Average Totals', lTitle = 'Studies', fTitle = 'moy_avg', fPath = fPath):
    """
    Plots a time-series graph of month of year averages of a study for a given MultiIndex Dataframe that follows calsim conventions. Calculates mean for 12 months across all study years and uses the plot_ts function to produce a graph.
    
    The function assumes the DataFrame columns follow a specific naming
    convention where the last part of the name indicates the study. 
    """
    df_copy = df.copy()
    df_copy["Month"] = df.index.month
    df_moy = df_copy.groupby('Month').mean()
    plot_ts(df_moy, pTitle = pTitle, xLab = xLab, lTitle = lTitle, fTitle = fTitle, fPath = fPath)

### Difference From Baseline

In [25]:
def get_difference_from_baseline(df):
    """
    Calculates the difference from baseline for a given variable
    Assumptions: baseline column on first column, df only contains single variable
    """
    df_diff = df.copy()
    baseline_column = df_diff.iloc[:, 0]
    
    for i in range(1, df_diff.shape[1]):
        df_diff.iloc[:, i] = df_diff.iloc[:, i].sub(baseline_column)
    df_diff = df_diff.iloc[:, 1:]

    return df_diff

In [26]:
def difference_from_baseline(df, plot_type, pTitle = 'Difference from Baseline ', xLab = 'Date', lTitle = 'Studies', fTitle = "___", pSave = True, fPath = fPath):
    """
    Plots the difference from baseline of a single variable with a specific plot type
    plot_type parameter inputs: plot_ts, plot_exceedance, plot_moy_averages, plot_annual_totals
    """
    pTitle += plot_type.__name__
    diff_df = get_difference_from_baseline(df)
    plot_type(diff_df, pTitle = pTitle, fTitle = fTitle, fPath = fPath)

In [27]:
def slice_with_baseline(df, var, study_lst):
    """
    Creates a subset of df based on varname and slices it according to the provided range.
    """
    subset_df = create_subset_var(df, var)
    df_baseline = subset_df.iloc[:,[0]]
    df_rest = subset_df.iloc[:, study_lst]
    return pd.concat([df_baseline, df_rest], axis = 1)

### Metrics

In [28]:
def plot_ts_regular(df, title):
    df.index = pd.to_datetime(df.index.year) 
    plt.figure(figsize=(10, 6))
    sns.lineplot(data=df, marker='o')
    plt.title(title)
    plt.ylabel('Mean Value')
    plt.xlabel('Year')
    plt.xticks(rotation=45)
    plt.tight_layout()
    plt.show()

##### Plot Mean annual SWP M&I  and total deliveries

In [29]:
# df_pmi = compute_annual_means(df, "DEL_SWP_PMI", [0], "TAF")
# plot_ts_regular(df_pmi, "Annual Mean PMI (TAF)")
# print(compute_mean(df, ["DEL_SWP_PMI"], [0], months = None))

In [30]:
# wet_df_pmi = compute_annual_means(wet_df, ["DEL_SWP_PMI"], [0])
# plot_ts_regular(wet_df_pmi, "Wet Annual Mean PMI (TAF)")
# print(compute_mean(wet_df, ["DEL_SWP_PMI"], [0], months = None))

In [31]:
# dry_df_pmi = compute_annual_means(dry_df, ["DEL_SWP_PMI"], [0])
# plot_ts_regular(dry_df_pmi, "Dry Annual Mean PMI (TAF)")
# print(compute_mean(dry_df, ["DEL_SWP_PMI"], [0], months = None))

#### Ann_Avg_SWPTotDel_TAF

In [32]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(df, "DEL_SWP_TOTAL", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Ann_Avg_SWPTotDel_TAF_df = pd.DataFrame(metrics, columns=['Ann_Avg_SWPTotDel_TAF'])
Ann_Avg_SWPTotDel_TAF_df

Ann_Avg_SWPTotDel_TAF
0              3450.959450
1              3499.658107
2              3373.532604
3              3302.689714
4              3170.088090
..                     ...
379            3303.151967
380            3550.437043
381            3603.345942
382            3494.594095
383            3270.001801

[384 rows x 1 columns]

In [33]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(wet_df, "DEL_SWP_TOTAL", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Wet_Ann_Avg_SWPTotDel_TAF_df = pd.DataFrame(metrics, columns=['Wet_Ann_Avg_SWPTotDel_TAF'])
Wet_Ann_Avg_SWPTotDel_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Wet_Ann_Avg_SWPTotDel_TAF
0                  3077.252636
1                  3130.378089
2                  3069.072979
3                  2982.667284
4                  2824.948289
..                         ...
379                2879.137753
380                3091.605278
381                3140.164379
382                3113.633455
383                2967.268158

[384 rows x 1 columns]

In [34]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(dry_df, "DEL_SWP_TOTAL", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Dry_Ann_Avg_SWPTotDel_TAF_df = pd.DataFrame(metrics, columns=['Dry_Ann_Avg_SWPTotDel_TAF'])
Dry_Ann_Avg_SWPTotDel_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Dry_Ann_Avg_SWPTotDel_TAF
0                  1706.727740
1                  1716.369619
2                  1577.817420
3                  1577.374411
4                  1570.570845
..                         ...
379                1732.360707
380                1866.628532
381                1890.741196
382                1732.072762
383                1540.737358

[384 rows x 1 columns]

#### Ann_Avg_CVPSCEXDel_TAF

In [35]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(df, "DEL_CVP_PSCEX_TOTAL", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Ann_Avg_CVPSCEXDel_TAF_df = pd.DataFrame(metrics, columns=['Ann_Avg_CVPSCEXDel_TAF'])
Ann_Avg_CVPSCEXDel_TAF_df

Ann_Avg_CVPSCEXDel_TAF
0               2459.309030
1               2459.632700
2               2457.731819
3               2442.197441
4               2391.434551
..                      ...
379             1751.301656
380             1733.438279
381             1753.193672
382             1740.472447
383             1714.613386

[384 rows x 1 columns]

In [36]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(wet_df, "DEL_CVP_PSCEX_TOTAL", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Wet_Ann_Avg_CVPSCEXDel_TAF_df = pd.DataFrame(metrics, columns=['Wet_Ann_Avg_CVPSCEXDel_TAF'])
Wet_Ann_Avg_CVPSCEXDel_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Wet_Ann_Avg_CVPSCEXDel_TAF
0                   1936.515222
1                   1936.745023
2                   1936.499048
3                   1936.587476
4                   1927.691025
..                          ...
379                 1387.299083
380                 1384.915317
381                 1386.841284
382                 1383.833451
383                 1383.109446

[384 rows x 1 columns]

In [37]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(dry_df, "DEL_CVP_PSCEX_TOTAL", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Dry_Ann_Avg_CVPSCEXDel_TAF_df = pd.DataFrame(metrics, columns=['Dry_Ann_Avg_CVPSCEXDel_TAF'])
Dry_Ann_Avg_CVPSCEXDel_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Dry_Ann_Avg_CVPSCEXDel_TAF
0                   1598.151569
1                   1598.399219
2                   1595.301621
3                   1566.862872
4                   1487.607434
..                          ...
379                 1125.726605
380                 1096.724725
381                 1129.855890
382                 1111.153320
383                 1065.110328

[384 rows x 1 columns]

#### Ann_Avg_SWPMIDel_TAF

In [38]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(df, "DEL_SWP_PMI", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Ann_Avg_SWPMIDel_TAF_df = pd.DataFrame(metrics, columns=['Ann_Avg_SWPMIDel_TAF'])
Ann_Avg_SWPMIDel_TAF_df

Ann_Avg_SWPMIDel_TAF
0             1757.988651
1             1799.105249
2             1744.720975
3             1731.348519
4             1678.806572
..                    ...
379           1897.831826
380           1994.077569
381           2034.115622
382           1978.595412
383           1856.246855

[384 rows x 1 columns]

In [39]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(wet_df, "DEL_SWP_PMI", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Wet_Ann_Avg_SWPMIDel_TAF_df = pd.DataFrame(metrics, columns=['Wet_Ann_Avg_SWPMIDel_TAF'])
Wet_Ann_Avg_SWPMIDel_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Wet_Ann_Avg_SWPMIDel_TAF
0                 1624.498655
1                 1663.075013
2                 1627.949137
3                 1590.037734
4                 1506.356995
..                        ...
379               1664.614506
380               1779.706347
381               1815.366542
382               1800.493884
383               1710.514100

[384 rows x 1 columns]

In [40]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(dry_df, "DEL_SWP_PMI", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Dry_Ann_Avg_SWPMIDel_TAF_df = pd.DataFrame(metrics, columns=['Dry_Ann_Avg_SWPMIDel_TAF'])
Dry_Ann_Avg_SWPMIDel_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Dry_Ann_Avg_SWPMIDel_TAF
0                  784.747989
1                  802.235657
2                  755.433952
3                  787.512231
4                  816.360449
..                        ...
379                979.845286
380                983.867454
381               1003.731615
382                924.705190
383                835.728831

[384 rows x 1 columns]

#### Ann_Avg_CVPRefDel_TAF

In [41]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(df, "DEL_CVP_PRF_TOTAL", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Ann_Avg_CVPRefDel_TAF_df = pd.DataFrame(metrics, columns=['Ann_Avg_CVPRefDel_TAF'])
Ann_Avg_CVPRefDel_TAF_df

Ann_Avg_CVPRefDel_TAF
0               376.185582
1               376.210216
2               376.240630
3               374.308095
4               367.869906
..                     ...
379             347.008747
380             340.627962
381             345.382773
382             347.693727
383             341.764999

[384 rows x 1 columns]

In [42]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(wet_df, "DEL_CVP_PRF_TOTAL", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Wet_Ann_Avg_CVPRefDel_TAF_df = pd.DataFrame(metrics, columns=['Ann_Avg_CVPRefDel_TAF'])
Wet_Ann_Avg_CVPRefDel_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Ann_Avg_CVPRefDel_TAF
0               300.118346
1               300.243718
2               300.512278
3               300.102889
4               297.707906
..                     ...
379             276.950027
380             277.461411
381             277.094334
382             280.263669
383             276.224393

[384 rows x 1 columns]

In [43]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(dry_df, "DEL_CVP_PRF_TOTAL", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Dry_Ann_Avg_CVPRefDel_TAF_df = pd.DataFrame(metrics, columns=['Ann_Avg_CVPRefDel_TAF'])
Dry_Ann_Avg_CVPRefDel_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Ann_Avg_CVPRefDel_TAF
0               238.650857
1               238.509081
2               238.164646
3               235.252671
4               227.086724
..                     ...
379             219.979232
380             207.590630
381             216.801489
382             216.293772
383             211.504345

[384 rows x 1 columns]

#### Ann_Avg_SWPAGDel_TAF

In [44]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(df, "DEL_SWP_PAG", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Ann_Avg_SWPAGDel_TAF_df = pd.DataFrame(metrics, columns=['Ann_Avg_SWPAGDel_TAF'])
Ann_Avg_SWPAGDel_TAF_df

Ann_Avg_SWPAGDel_TAF
0             1628.482302
1             1636.064364
2             1564.325251
3             1506.898363
4             1427.022581
..                    ...
379           1340.820259
380           1491.859595
381           1504.741829
382           1451.510184
383           1349.266452

[384 rows x 1 columns]

In [45]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(wet_df, "DEL_SWP_PAG", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Wet_Ann_Avg_SWPAGDel_TAF_df = pd.DataFrame(metrics, columns=['Wet_Ann_Avg_SWPAGDel_TAF'])
Wet_Ann_Avg_SWPAGDel_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Wet_Ann_Avg_SWPAGDel_TAF
0                 1402.708307
1                 1417.257407
2                 1391.078165
3                 1342.587751
4                 1268.561461
..                        ...
379               1164.463635
380               1261.839326
381               1274.752172
382               1263.093893
383               1206.708386

[384 rows x 1 columns]

In [46]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(dry_df, "DEL_SWP_PAG", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Dry_Ann_Avg_SWPAGDel_TAF_df = pd.DataFrame(metrics, columns=['Dry_Ann_Avg_SWPAGDel_TAF'])
Dry_Ann_Avg_SWPAGDel_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Dry_Ann_Avg_SWPAGDel_TAF
0                  878.979826
1                  871.134036
2                  779.387413
3                  746.939698
4                  711.605195
..                        ...
379                709.515504
380                839.761154
381                844.009656
382                764.367650
383                662.008605

[384 rows x 1 columns]

##### Average end-of-September NOD reservoir storage Sep_Avg_NODstorage_TAF

In [47]:
# change to TAF Later, temporarily in CFS because of error in Extract notebook

In [48]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(df, "S_RESTOT_NOD", [study_index], "TAF", months=[9])
    metrics.append(metric_value)

Sep_Avg_NODstorage_TAF_df = pd.DataFrame(metrics, columns=['Sep_Avg_NODstorage_TAF'])
Sep_Avg_NODstorage_TAF_df

Sep_Avg_NODstorage_TAF
0               6680.744502
1               6885.186129
2               5736.111245
3               4249.038200
4               2507.414995
..                      ...
379             5106.061509
380             7632.463580
381             7698.671449
382             6906.952343
383             5683.356195

[384 rows x 1 columns]

In [49]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(wet_df, "S_RESTOT_NOD", [study_index], "TAF", months=[9])
    metrics.append(metric_value)

Wet_Sep_Avg_NODstorage_TAF_df = pd.DataFrame(metrics, columns=['Wet_Sep_Avg_NODstorage_TAF'])
Wet_Sep_Avg_NODstorage_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Wet_Sep_Avg_NODstorage_TAF
0                   7635.913462
1                   7793.766069
2                   6718.099442
3                   5151.678883
4                   3144.668790
..                          ...
379                 5596.746771
380                 8533.305763
381                 8520.207698
382                 7769.070673
383                 6423.216873

[384 rows x 1 columns]

In [50]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(dry_df, "S_RESTOT_NOD", [study_index], "TAF", months=[9])
    metrics.append(metric_value)

Dry_Sep_Avg_NODstorage_TAF_df = pd.DataFrame(metrics, columns=['Dry_Sep_Avg_NODstorage_TAF'])
Dry_Sep_Avg_NODstorage_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Dry_Sep_Avg_NODstorage_TAF
0                   5025.118307
1                   5310.314233
2                   4033.998370
3                   2684.461017
4                   1402.841749
..                          ...
379                 4255.540387
380                 6071.003797
381                 6274.675283
382                 5412.613903
383                 4400.931020

[384 rows x 1 columns]

##### Average end-of-April NOD reservoir storage Apr_Avg_NODstorage_TAF

In [51]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(df, "S_RESTOT_NOD", [study_index], "TAF", months=[4])
    metrics.append(metric_value)

Apr_Avg_NODstorage_TAF_df = pd.DataFrame(metrics, columns=['Apr_Avg_NODstorage_TAF'])
Apr_Avg_NODstorage_TAF_df

Apr_Avg_NODstorage_TAF
0               9478.750280
1               9395.367171
2               8038.145646
3               6402.984684
4               4469.111422
..                      ...
379             6576.077626
380             9892.395779
381             9791.516388
382             8830.697422
383             7508.309970

[384 rows x 1 columns]

In [52]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(wet_df, "S_RESTOT_NOD", [study_index], "TAF", months=[4])
    metrics.append(metric_value)

Wet_Apr_Avg_NODstorage_TAF_df = pd.DataFrame(metrics, columns=['Wet_Apr_Avg_NODstorage_TAF'])
Wet_Apr_Avg_NODstorage_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Wet_Apr_Avg_NODstorage_TAF
0                  10422.311644
1                  10277.471240
2                   8938.845827
3                   7273.123842
4                   5196.416006
..                          ...
379                 7012.446875
380                10603.757260
381                10487.154260
382                 9583.069467
383                 8176.039037

[384 rows x 1 columns]

In [53]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(dry_df, "S_RESTOT_NOD", [study_index], "TAF", months=[4])
    metrics.append(metric_value)

Dry_Apr_Avg_NODstorage_TAF_df = pd.DataFrame(metrics, columns=['Dry_Apr_Avg_NODstorage_TAF'])
Dry_Apr_Avg_NODstorage_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Dry_Apr_Avg_NODstorage_TAF
0                   7843.243917
1                   7866.386783
2                   6476.932000
3                   4894.743477
4                   3208.450143
..                          ...
379                 5819.704260
380                 8659.369213
381                 8585.744077
382                 7526.585877
383                 6350.912920

[384 rows x 1 columns]

##### Average end-of-April Shasta reservoir storage Apr_Avg_ShstaStorage_TAF

In [54]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(df, "S_SHSTA_", [study_index], "TAF", months=[4])
    metrics.append(metric_value)

Apr_Avg_ShstaStorage_TAF_df = pd.DataFrame(metrics, columns=['Apr_Avg_ShstaStorage_TAF'])
Apr_Avg_ShstaStorage_TAF_df

Apr_Avg_ShstaStorage_TAF
0                 4103.715194
1                 4137.956748
2                 3592.731022
3                 2763.109577
4                 1788.753759
..                        ...
379               3043.275879
380               4226.326320
381               4247.962102
382               3932.706646
383               3414.607076

[384 rows x 1 columns]

In [55]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(wet_df, "S_SHSTA_", [study_index], "TAF", months=[4])
    metrics.append(metric_value)

Wet_Apr_Avg_ShstaStorage_TAF_df = pd.DataFrame(metrics, columns=['Wet_Apr_Avg_ShstaStorage_TAF'])
Wet_Apr_Avg_ShstaStorage_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Wet_Apr_Avg_ShstaStorage_TAF
0                     4370.067025
1                     4324.351954
2                     3695.130408
3                     2859.044740
4                     1865.312487
..                            ...
379                   2879.493629
380                   4403.942310
381                   4370.306992
382                   3962.655304
383                   3357.092938

[384 rows x 1 columns]

In [56]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(dry_df, "S_SHSTA_", [study_index], "TAF", months=[4])
    metrics.append(metric_value)

Dry_Apr_Avg_ShstaStorage_TAF_df = pd.DataFrame(metrics, columns=['Dry_Apr_Avg_ShstaStorage_TAF'])
Dry_Apr_Avg_ShstaStorage_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Dry_Apr_Avg_ShstaStorage_TAF
0                     3642.038687
1                     3814.871723
2                     3415.238753
3                     2596.821960
4                     1656.051964
..                            ...
379                   3327.165113
380                   3918.458603
381                   4035.897627
382                   3880.795640
383                   3514.298247

[384 rows x 1 columns]

##### Average end-of-April Oroville reservoir storage Apr_Avg_OrovlStorage_TAF

In [57]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(df, "S_OROVL_", [study_index], "TAF", months=[4])
    metrics.append(metric_value)

Apr_Avg_OrovlStorage_TAF_df = pd.DataFrame(metrics, columns=['Apr_Avg_OrovlStorage_TAF'])
Apr_Avg_OrovlStorage_TAF_df

Apr_Avg_OrovlStorage_TAF
0                 2749.799326
1                 2625.274924
2                 2176.265243
3                 1829.999037
4                 1440.410153
..                        ...
379               1703.758066
380               2928.842401
381               2818.036627
382               2391.557004
383               1958.330077

[384 rows x 1 columns]

In [58]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(wet_df, "S_OROVL_", [study_index], "TAF", months=[4])
    metrics.append(metric_value)

Wet_Apr_Avg_OrovlStorage_TAF_df = pd.DataFrame(metrics, columns=['Wet_Apr_Avg_OrovlStorage_TAF'])
Wet_Apr_Avg_OrovlStorage_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Wet_Apr_Avg_OrovlStorage_TAF
0                     3160.976640
1                     3067.384721
2                     2673.573612
3                     2308.934754
4                     1860.945259
..                            ...
379                   2086.088331
380                   3245.122950
381                   3177.417077
382                   2849.918315
383                   2409.779267

[384 rows x 1 columns]

In [59]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(dry_df, "S_OROVL_", [study_index], "TAF", months=[4])
    metrics.append(metric_value)

Dry_Apr_Avg_OrovlStorage_TAF_df = pd.DataFrame(metrics, columns=['Dry_Apr_Avg_OrovlStorage_TAF'])
Dry_Apr_Avg_OrovlStorage_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Dry_Apr_Avg_OrovlStorage_TAF
0                     2037.091980
1                     1858.951277
2                     1314.264070
3                      999.843793
4                      711.482635
..                            ...
379                   1041.052273
380                   2380.622783
381                   2195.110513
382                   1597.064065
383                   1175.818149

[384 rows x 1 columns]

##### Average Annual Delta Outflow Ann_Avg_NDO_TAF

In [60]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(df, "NDO", [study_index], "TAF", months=None)
    metrics.append(metric_value)
Ann_Avg_NDO_TAF_df = pd.DataFrame(metrics, columns=['Ann_Avg_NDO_TAF'])
Ann_Avg_NDO_TAF_df

Ann_Avg_NDO_TAF
0       15444.331737
1       15791.118131
2       16972.322632
3       18013.577765
4       19001.697923
..               ...
379     19825.923292
380     16604.427187
381     16980.033117
382     17882.338341
383     18700.229940

[384 rows x 1 columns]

In [61]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(wet_df, "NDO", [study_index], "TAF", months=None)
    metrics.append(metric_value)
Wet_Ann_Avg_NDO_TAF_df = pd.DataFrame(metrics, columns=['Wet_Ann_Avg_NDO_TAF'])
Wet_Ann_Avg_NDO_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Wet_Ann_Avg_NDO_TAF
0           15906.292775
1           16151.946812
2           17256.020846
3           18294.051585
4           19359.552591
..                   ...
379         20107.568364
380         17149.422373
381         17408.926390
382         18164.737476
383         18938.585398

[384 rows x 1 columns]

In [62]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(dry_df, "NDO", [study_index], "TAF", months=None)
    metrics.append(metric_value)
Dry_Ann_Avg_NDO_TAF_df = pd.DataFrame(metrics, columns=['Dry_Ann_Avg_NDO_TAF'])
Dry_Ann_Avg_NDO_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Dry_Ann_Avg_NDO_TAF
0            4460.301922
1            4726.472231
2            5235.045759
3            5586.931569
4            5801.093468
..                   ...
379          6189.302879
380          4723.371786
381          5021.436609
382          5540.318513
383          5878.525186

[384 rows x 1 columns]

##### Fall (Sep-Nov) average salinity, as indicated by X2 distance (flip sign) Fall_Avg_X2_KM

In [63]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(df, "X2_PRV", [study_index], "KM", months=[9, 10, 11]) * -1 / 3
    metrics.append(metric_value)

Fall_Avg_X2_KM_df = pd.DataFrame(metrics, columns=['Fall_Avg_X2_KM'])
Fall_Avg_X2_KM_df

Fall_Avg_X2_KM
0        -85.618250
1        -85.734801
2        -85.941630
3        -85.995324
4        -85.959160
..              ...
379      -93.353249
380      -84.688441
381      -84.805526
382      -85.406842
383      -85.681525

[384 rows x 1 columns]

In [64]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(wet_df, "X2_PRV", [study_index], "KM", months=[9, 10, 11]) * -1 / 3
    metrics.append(metric_value)

Wet_Fall_Avg_X2_KM_df = pd.DataFrame(metrics, columns=['Wet_Fall_Avg_X2_KM'])
Wet_Fall_Avg_X2_KM_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Wet_Fall_Avg_X2_KM
0            -63.915478
1            -64.022096
2            -64.399371
3            -64.512845
4            -64.428168
..                  ...
379          -71.165005
380          -63.080328
381          -63.279356
382          -63.987443
383          -64.300420

[384 rows x 1 columns]

In [65]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(dry_df, "X2_PRV", [study_index], "KM", months=[9, 10, 11]) * -1 / 3
    metrics.append(metric_value)

Dry_Fall_Avg_X2_KM_df = pd.DataFrame(metrics, columns=['Dry_Fall_Avg_X2_KM'])
Dry_Fall_Avg_X2_KM_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Dry_Fall_Avg_X2_KM
0            -60.852434
1            -60.906073
2            -60.721241
3            -60.650133
4            -60.710310
..                  ...
379          -64.153581
380          -60.401560
381          -60.318584
382          -60.360053
383          -60.394598

[384 rows x 1 columns]

##### Spring (Mar-May) average salinity, as indicated by X2 distance (flip sign) Spring_Avg_X2_KM

In [66]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(df, "X2_PRV", [study_index], "KM", months=[3, 4, 5]) * -1 / 3
    metrics.append(metric_value)

Spring_Avg_X2_KM_df = pd.DataFrame(metrics, columns=['Spring_Avg_X2_KM'])
Spring_Avg_X2_KM_df

Spring_Avg_X2_KM
0          -61.806239
1          -61.499069
2          -60.317475
3          -59.398004
4          -58.437343
..                ...
379        -56.789920
380        -61.066408
381        -60.605220
382        -59.590128
383        -58.778897

[384 rows x 1 columns]

In [67]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(wet_df, "X2_PRV", [study_index], "KM", months=[3, 4, 5]) * -1 / 3
    metrics.append(metric_value)

Wet_Spring_Avg_X2_KM_df = pd.DataFrame(metrics, columns=['Wet_Spring_Avg_X2_KM'])
Wet_Spring_Avg_X2_KM_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Wet_Spring_Avg_X2_KM
0              -55.751436
1              -55.570829
2              -54.783512
3              -54.012084
4              -53.143892
..                    ...
379            -52.256071
380            -55.037828
381            -54.862396
382            -54.282796
383            -53.641341

[384 rows x 1 columns]

In [68]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(dry_df, "X2_PRV", [study_index], "KM", months=[3, 4, 5]) * -1 / 3
    metrics.append(metric_value)

Dry_Spring_Avg_X2_KM_df = pd.DataFrame(metrics, columns=['Dry_Spring_Avg_X2_KM'])
Dry_Spring_Avg_X2_KM_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Dry_Spring_Avg_X2_KM
0              -72.301231
1              -71.774687
2              -69.909677
3              -68.733600
4              -67.612659
..                    ...
379            -64.648591
380            -71.515945
381            -70.559448
382            -68.789504
383            -67.683993

[384 rows x 1 columns]

##### Mean annual SWP MWD delivery volume (not used)

In [69]:
# metrics = []

# for study_index in np.arange(0, len(dss_names)):
#     metric_value = compute_mean(df, ["DEL_SWP_MWD"], [study_index], months=None)
#     metrics.append(metric_value)

# mwd_results_df = pd.DataFrame(metrics, columns=['SWP MWD Delivery Mean (TAF)'])
# mwd_results_df

In [70]:
# wet_metrics = []

# for study_index in np.arange(0, len(dss_names)):
#     metric_value = compute_mean(wet_df, ["DEL_SWP_MWD"], [study_index], months=None)
#     wet_metrics.append(metric_value)

# wet_mwd_results_df = pd.DataFrame(wet_metrics, columns=['Wet SWP MWD Delivery Mean (TAF)'])
# wet_mwd_results_df

In [71]:
# dry_metrics = []

# for study_index in np.arange(0, len(dss_names)):
#     metric_value = compute_mean(dry_df, ["DEL_SWP_MWD"], [study_index], months=None)
#     dry_metrics.append(metric_value)

# dry_mwd_results_df = pd.DataFrame(dry_metrics, columns=['Dry SWP MWD Delivery Mean (TAF)'])
# dry_mwd_results_df

#### Ann_Avg_CVPTotDel_TAF

In [72]:
df_cvptot = create_subset_unit(df, "DEL_CVP_TOTAL", "TAF").iloc[:, :600]

In [73]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(df_cvptot, "DEL_CVP_TOTAL", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Ann_Avg_CVPTotDel_TAF_df = pd.DataFrame(metrics, columns=['Ann_Avg_CVPTotDel_TAF'])
Ann_Avg_CVPTotDel_TAF_df

Ann_Avg_CVPTotDel_TAF
0              2186.902364
1              2628.024274
2              4814.926628
3              2192.581719
4              2793.895111
..                     ...
379            2687.689237
380            4719.718445
381            1970.701043
382            2563.324840
383            4534.025862

[384 rows x 1 columns]

In [74]:
wet_df_cvptot = create_subset_unit(wet_df, "DEL_CVP_TOTAL", "TAF").iloc[:, :600]

In [75]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(wet_df_cvptot, "DEL_CVP_TOTAL", [study_index], "TAF")
    metrics.append(metric_value)

Wet_Ann_Avg_CVPTotDel_TAF_df = pd.DataFrame(metrics, columns=['Wet_Ann_Avg_CVPTotDel_TAF'])
Wet_Ann_Avg_CVPTotDel_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Wet_Ann_Avg_CVPTotDel_TAF
0                  1766.082730
1                  2291.359757
2                  4057.442483
3                  1768.608343
4                  2410.212636
..                         ...
379                2286.933716
380                3922.970091
381                1591.472785
382                2175.202438
383                3766.675200

[384 rows x 1 columns]

In [76]:
dry_df_cvptot = create_subset_unit(dry_df, "DEL_CVP_TOTAL", "TAF").iloc[:, :600]

In [77]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(dry_df_cvptot, "DEL_CVP_TOTAL", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Dry_Ann_Avg_CVPTotDel_TAF_df = pd.DataFrame(metrics, columns=['Dry_Ann_Avg_CVPTotDel_TAF'])
Dry_Ann_Avg_CVPTotDel_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Dry_Ann_Avg_CVPTotDel_TAF
0                  1355.521133
1                  1377.264150
2                  2732.785270
3                  1362.109822
4                  1502.558943
..                         ...
379                1492.576855
380                2759.509253
381                1221.529088
382                1432.312746
383                2653.841829

[384 rows x 1 columns]

#### Ann_Avg_CVPAgDel_TAF

In [78]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(df, "DEL_CVP_PAG_TOTAL", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Ann_Avg_CVPAgDel_TAF_df = pd.DataFrame(metrics, columns=['Ann_Avg_CVPAgDel_TAF'])
Ann_Avg_CVPAgDel_TAF_df

Ann_Avg_CVPAgDel_TAF
0             1460.060352
1             1625.425898
2             1426.223396
3              932.899995
4              544.774300
..                    ...
379            730.220384
380           1453.834651
381           1480.344975
382           1473.919683
383           1445.720059

[384 rows x 1 columns]

In [79]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(wet_df, "DEL_CVP_PAG_TOTAL", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Wet_Ann_Avg_CVPAgDel_TAF_df = pd.DataFrame(metrics, columns=['Wet_Ann_Avg_CVPAgDel_TAF'])
Wet_Ann_Avg_CVPAgDel_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Wet_Ann_Avg_CVPAgDel_TAF
0                 1403.798510
1                 1521.121829
2                 1336.481819
3                  879.611376
4                  477.244672
..                        ...
379                656.104873
380               1184.024935
381               1186.886683
382               1186.681484
383               1182.979512

[384 rows x 1 columns]

In [80]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(dry_df, "DEL_CVP_PAG_TOTAL", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Dry_Ann_Avg_CVPAgDel_TAF_df = pd.DataFrame(metrics, columns=['Dry_Ann_Avg_CVPAgDel_TAF'])
Dry_Ann_Avg_CVPAgDel_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Dry_Ann_Avg_CVPAgDel_TAF
0                  570.454417
1                  697.105802
2                  609.023036
3                  390.307497
4                  282.135547
..                        ...
379                353.756555
380                886.328239
381                930.375115
382                918.972324
383                873.098166

[384 rows x 1 columns]

#### Ann_Avg_BanksJones_TAF

In [81]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(df, "D_TOTAL", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Ann_Avg_BanksJones_TAF_df = pd.DataFrame(metrics, columns=['Ann_Avg_BanksJones_TAF'])
Ann_Avg_BanksJones_TAF_df

Ann_Avg_BanksJones_TAF
0               5314.467080
1               5221.043788
2               5033.508183
3               4691.966771
4               4390.240189
..                      ...
379             4266.125713
380             5529.574347
381             5267.458606
382             5087.597465
383             4827.143652

[384 rows x 1 columns]

In [82]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(wet_df, "D_TOTAL", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Wet_Ann_Avg_BanksJones_TAF_df = pd.DataFrame(metrics, columns=['Wet_Ann_Avg_BanksJones_TAF'])
Wet_Ann_Avg_BanksJones_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Wet_Ann_Avg_BanksJones_TAF
0                   4893.699803
1                   4777.750379
2                   4498.541516
3                   4113.511963
4                   3763.543704
..                          ...
379                 3670.790773
380                 4885.803376
381                 4635.745252
382                 4457.739276
383                 4178.627063

[384 rows x 1 columns]

In [83]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(dry_df, "D_TOTAL", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Dry_Ann_Avg_BanksJones_TAF_df = pd.DataFrame(metrics, columns=['Dry_Ann_Avg_BanksJones_TAF'])
Dry_Ann_Avg_BanksJones_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Dry_Ann_Avg_BanksJones_TAF
0                   2397.964750
1                   2400.362562
2                   2474.341987
3                   2425.243858
4                   2396.494830
..                          ...
379                 2308.429482
380                 2801.694895
381                 2696.370529
382                 2633.654682
383                 2574.617028

[384 rows x 1 columns]

##### NEW VARIABLES - Can's New

##### Variability in Fall (Oct) salinity, as indicated by X2 distance - Oct_StDev_X2

In [84]:
Oct_StDev_X2 = compute_sd(df, "X2_PRV", "KM", "Oct_StDev_X2", months=[10])
Oct_StDev_X2

Oct_StDev_X2
0        6.542445
1        6.414817
2        5.933861
3        5.909413
4        5.926163
..            ...
595      8.176955
596      7.965440
597      5.983565
598      5.058976
599      4.241868

[600 rows x 1 columns]

In [85]:
Wet_Oct_StDev_X2 = compute_sd(wet_df, "X2_PRV", "KM", "Wet_Oct_StDev_X2", months=[10])
Wet_Oct_StDev_X2

Wet_Oct_StDev_X2
0            5.568378
1            5.453050
2            5.063713
3            5.153217
4            5.193537
..                ...
595          7.781114
596          7.991051
597          5.958152
598          5.233495
599          4.572587

[600 rows x 1 columns]

In [86]:
Dry_Oct_StDev_X2 = compute_sd(dry_df, "X2_PRV", "KM", "Dry_Oct_StDev_X2", months=[10])
Dry_Oct_StDev_X2

Dry_Oct_StDev_X2
0            0.864057
1            1.059890
2            1.091209
3            1.000563
4            1.209964
..                ...
595          3.561314
596          3.642758
597          3.373395
598          2.597599
599          2.005620

[600 rows x 1 columns]

##### Variability in Spring (Apr) salinity, as indicated by X2 distance - Apr_StDev_X2

In [87]:
Apr_StDev_X2 = compute_sd(df, "X2_PRV", "KM", "Apr_StDev_X2", months=[4])
Apr_StDev_X2

Apr_StDev_X2
0       10.346875
1       10.206163
2        9.572897
3        9.231497
4        8.921624
..            ...
595     10.292074
596      9.747449
597      9.091666
598      8.797966
599      8.375252

[600 rows x 1 columns]

In [88]:
Wet_Apr_StDev_X2 = compute_sd(wet_df, "X2_PRV", "KM", "Wet_Apr_StDev_X2", months=[4])
Wet_Apr_StDev_X2

Wet_Apr_StDev_X2
0            6.840707
1            6.835749
2            6.480162
3            6.082184
4            5.488018
..                ...
595          6.404587
596          6.433001
597          6.131643
598          5.467307
599          4.883527

[600 rows x 1 columns]

In [89]:
Dry_Apr_StDev_X2 = compute_sd(dry_df, "X2_PRV", "KM", "Dry_Apr_StDev_X2", months=[4])
Dry_Apr_StDev_X2

Dry_Apr_StDev_X2
0            7.934651
1            8.220776
2            8.138063
3            8.131305
4            8.273841
..                ...
595          9.136112
596          8.694704
597          8.241827
598          8.404734
599          8.402864

[600 rows x 1 columns]

##### New Functions to Automate Abhinav's Calculations

In [90]:
def calculate_exceedance_probabilities(df):
    exceedance_df = pd.DataFrame(index=df.index)
    
    for column in df.columns:
        # ASK JAMES if he said 1 - the formula below - would make sense considering the range of sensible values.
        #sort data, use formula: rank/(1+n), n = number of data points (82)
        sorted_values = df[column].sort_values(ascending=False)
        exceedance_probs = (sorted_values.rank(method='first', ascending=False)) / (1 + len(sorted_values))
        exceedance_df[column] = exceedance_probs.sort_index()

    return exceedance_df

In [91]:
def exceedance_probability(df, var, threshold, month, vartitle):
    var_df = create_subset_var(df, var)
    var_month_df = var_df[var_df.index.month.isin([month])]
    result_df = count_exceedance_days(var_month_df, threshold) / len(var_month_df) * 100
    reshaped_df = result_df.melt(value_name=vartitle).reset_index(drop=True)[[vartitle]]
    return reshaped_df

In [92]:
def exceedance_metric(df, var, exceedance_percent, vartitle, unit):
    var_df = create_subset_unit(df, var, unit)
    annual_flows = calculate_flow_sum_per_year(var_df).iloc[:, 1:]
    exceedance_probs = calculate_exceedance_probabilities(annual_flows)

    annual_flows_sorted = annual_flows.apply(np.sort, axis=0)[::-1]
    exceedance_prob_baseline = exceedance_probs.apply(np.sort, axis=0).iloc[:, 0].to_frame()
    exceedance_prob_baseline.columns = ["Exceedance Sorted"]
    
    exceeding_index = exceedance_prob_baseline[exceedance_prob_baseline['Exceedance Sorted'] >= exceedance_percent].index[0]
    baseline_threshold = annual_flows_sorted.iloc[len(annual_flows_sorted) - exceeding_index - 1, 0]
        
    result_df = count_exceedance_days(annual_flows, baseline_threshold) / len(annual_flows) * 100
    reshaped_df = result_df.melt(value_name=vartitle).reset_index(drop=True)[[vartitle]]

    return reshaped_df

In [93]:
# var_df = create_subset_unit(wet_df, "DEL_CVP_PAG_N", "TAF")
# annual_flows = calculate_flow_sum_per_year(var_df).iloc[:, 1:]
# annual_flows
# exceedance_probs = calculate_exceedance_probabilities(annual_flows)
# 
# annual_flows_sorted = annual_flows.apply(np.sort, axis=0)[::-1]
# annual_flows_sorted
# exceedance_prob_baseline = exceedance_probs.apply(np.sort, axis=0).iloc[:, 0].to_frame()
# exceedance_prob_baseline.columns = ["Exceedance Sorted"]
# exceedance_prob_baseline
# exceeding_index = exceedance_prob_baseline[exceedance_prob_baseline['Exceedance Sorted'] >= 0.9].index[0]
# baseline_threshold = annual_flows_sorted.iloc[len(annual_flows_sorted) - exceeding_index - 1, 0]

In [94]:
# annual_flows_sorted

In [95]:
# exceedance_prob_baseline

In [96]:
# exceeding_index 

In [97]:
# baseline_threshold 

In [98]:
# count_exceedance_days(annual_flows, baseline_threshold)

### NEW VARIABLES - Assigned Can in June Sheet

##### Probability of SWP M&I Total annual delivery above specified threshold - Ann_Prob_SWPMIgtBL90

In [99]:
Ann_Prob_SWPMIgtBL90 = exceedance_metric(df, "DEL_SWP_PMI", 0.90, "Ann_Prob_SWPMIgtBL90", "TAF")
Ann_Prob_SWPMIgtBL90

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Date'] = pd.to_datetime(df.index)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Year'] = df['Date'].dt.year
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row

Ann_Prob_SWPMIgtBL90
0                8.536585
1                9.756098
2               13.414634
3               15.853659
4               12.195122
..                    ...
595             39.024390
596             42.682927
597             42.682927
598             35.365854
599             19.512195

[600 rows x 1 columns]

In [100]:
Wet_Ann_Prob_SWPMIgtBL90 = exceedance_metric(wet_df, "DEL_SWP_PMI", 0.90, "Wet_Ann_Prob_SWPMIgtBL90", "TAF")
Wet_Ann_Prob_SWPMIgtBL90

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Date'] = pd.to_datetime(df.index)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Year'] = df['Date'].dt.year
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row

Wet_Ann_Prob_SWPMIgtBL90
0                    7.462687
1                    8.955224
2                   16.417910
3                   16.417910
4                   13.432836
..                        ...
595                 35.820896
596                 38.805970
597                 38.805970
598                 32.835821
599                 22.388060

[600 rows x 1 columns]

In [101]:
Dry_Ann_Prob_SWPMIgtBL90 = exceedance_metric(dry_df, "DEL_SWP_PMI", 0.90, "Dry_Ann_Prob_SWPMIgtBL90", "TAF")
Dry_Ann_Prob_SWPMIgtBL90

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Date'] = pd.to_datetime(df.index)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Year'] = df['Date'].dt.year
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row

Dry_Ann_Prob_SWPMIgtBL90
0                    6.666667
1                   11.111111
2                    4.444444
3                    2.222222
4                    2.222222
..                        ...
595                 55.555556
596                 53.333333
597                 53.333333
598                 48.888889
599                 42.222222

[600 rows x 1 columns]

##### Probability of CVP NOD M&I contractors annual delivery above specified threshold - Ann_Prob_CVPMINgtBL90

In [102]:
Ann_Prob_CVPMINgtBL90 = exceedance_metric(df, "DEL_CVP_PMI_N", 0.90, "Ann_Prob_CVPMINgtBL90", "TAF")
Ann_Prob_CVPMINgtBL90

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Date'] = pd.to_datetime(df.index)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Year'] = df['Date'].dt.year
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row

Ann_Prob_CVPMINgtBL90
0                 8.536585
1                10.975610
2                 1.219512
3                 0.000000
4                 0.000000
..                     ...
595              20.731707
596              21.951220
597              17.073171
598               8.536585
599               2.439024

[600 rows x 1 columns]

In [103]:
Wet_Ann_Prob_CVPMINgtBL90 = exceedance_metric(wet_df, "DEL_CVP_PMI_N", 0.90, "Wet_Ann_Prob_CVPMINgtBL90", "TAF")
Wet_Ann_Prob_CVPMINgtBL90

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Date'] = pd.to_datetime(df.index)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Year'] = df['Date'].dt.year
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row

Wet_Ann_Prob_CVPMINgtBL90
0                     7.462687
1                     7.462687
2                     1.492537
3                     0.000000
4                     0.000000
..                         ...
595                  10.447761
596                  10.447761
597                  10.447761
598                   8.955224
599                   2.985075

[600 rows x 1 columns]

In [104]:
Dry_Ann_Prob_CVPMINgtBL90 =exceedance_metric(dry_df, "DEL_CVP_PMI_N", 0.90, "Dry_Ann_Prob_CVPMINgtBL90", "TAF")
Dry_Ann_Prob_CVPMINgtBL90

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Date'] = pd.to_datetime(df.index)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Year'] = df['Date'].dt.year
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row

Dry_Ann_Prob_CVPMINgtBL90
0                     6.666667
1                    11.111111
2                     2.222222
3                     0.000000
4                     0.000000
..                         ...
595                  46.666667
596                  48.888889
597                  26.666667
598                  11.111111
599                   2.222222

[600 rows x 1 columns]

##### Probability of CVP SOD M&I contractors annual delivery above specified threshold

In [105]:
Ann_Prob_CVPMISgtBL90 = exceedance_metric(df, "DEL_CVP_PMI_S", 0.90, "Ann_Prob_CVPMISgtBL90", "TAF")
Ann_Prob_CVPMISgtBL90

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Date'] = pd.to_datetime(df.index)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Year'] = df['Date'].dt.year
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row

Ann_Prob_CVPMISgtBL90
0                 3.658537
1                 3.658537
2                 1.219512
3                 0.000000
4                 0.000000
..                     ...
595              17.073171
596              18.292683
597              18.292683
598              18.292683
599              18.292683

[600 rows x 1 columns]

In [106]:
Wet_Ann_Prob_CVPMISgtBL90 = exceedance_metric(wet_df, "DEL_CVP_PMI_S", 0.90, "Wet_Ann_Prob_CVPMISgtBL90", "TAF")
Wet_Ann_Prob_CVPMISgtBL90

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Date'] = pd.to_datetime(df.index)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Year'] = df['Date'].dt.year
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row

Wet_Ann_Prob_CVPMISgtBL90
0                     4.477612
1                     4.477612
2                     1.492537
3                     0.000000
4                     0.000000
..                         ...
595                  13.432836
596                  13.432836
597                  13.432836
598                  13.432836
599                  13.432836

[600 rows x 1 columns]

In [107]:
Dry_Ann_Prob_CVPMISgtBL90 = exceedance_metric(dry_df, "DEL_CVP_PMI_S", 0.90, "Dry_Ann_Prob_CVPMISgtBL90", "TAF")
Dry_Ann_Prob_CVPMISgtBL90

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Date'] = pd.to_datetime(df.index)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Year'] = df['Date'].dt.year
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row

Dry_Ann_Prob_CVPMISgtBL90
0                     6.666667
1                    13.333333
2                     8.888889
3                     2.222222
4                     0.000000
..                         ...
595                  33.333333
596                  33.333333
597                  33.333333
598                  33.333333
599                  33.333333

[600 rows x 1 columns]

##### Frequency or probability of Shasta storage above thresholds for reliable cold water control - Apr_Prob_SHSTAgt38

In [108]:
Apr_Prob_SHSTAgt38 = exceedance_probability(df, "S_SHSTA_", 3800, 4, "Apr_Prob_SHSTAgt38")
Apr_Prob_SHSTAgt38

Apr_Prob_SHSTAgt38
0             81.707317
1             80.487805
2             51.219512
3              9.756098
4              1.219512
..                  ...
595           90.243902
596           93.902439
597           81.707317
598           62.195122
599           14.634146

[600 rows x 1 columns]

In [109]:
Wet_Apr_Prob_SHSTAgt38 = exceedance_probability(wet_df, "S_SHSTA_", 3800, 4, "Wet_Apr_Prob_SHSTAgt38")
Wet_Apr_Prob_SHSTAgt38

Wet_Apr_Prob_SHSTAgt38
0                 98.076923
1                 90.384615
2                 57.692308
3                 13.461538
4                  1.923077
..                      ...
595              100.000000
596               96.153846
597               78.846154
598               53.846154
599               11.538462

[600 rows x 1 columns]

In [110]:
Dry_Apr_Prob_SHSTAgt38 = exceedance_probability(dry_df, "S_SHSTA_", 3800, 4, "Dry_Apr_Prob_SHSTAgt38")
Dry_Apr_Prob_SHSTAgt38

Dry_Apr_Prob_SHSTAgt38
0                 53.333333
1                 63.333333
2                 40.000000
3                  3.333333
4                  0.000000
..                      ...
595               73.333333
596               90.000000
597               86.666667
598               76.666667
599               20.000000

[600 rows x 1 columns]

##### Probability of CVP NOD ag contractors annual delivery above specified threshold - Ann_Prob_CVPSCgtBL90

In [111]:
Ann_Prob_CVPSCgtBL90 = exceedance_metric(df, "DEL_CVP_PSC_N", 0.90, "Ann_Prob_CVPSCgtBL90", "TAF")
Ann_Prob_CVPSCgtBL90

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Date'] = pd.to_datetime(df.index)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Year'] = df['Date'].dt.year
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row

Ann_Prob_CVPSCgtBL90
0                8.536585
1                8.536585
2                9.756098
3                9.756098
4                4.878049
..                    ...
595              0.000000
596              0.000000
597              0.000000
598              0.000000
599              0.000000

[600 rows x 1 columns]

In [112]:
Wet_Ann_Prob_CVPSCgtBL90 = exceedance_metric(wet_df, "DEL_CVP_PSC_N", 0.90, "Wet_Ann_Prob_CVPSCgtBL90", "TAF")
Wet_Ann_Prob_CVPSCgtBL90

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Date'] = pd.to_datetime(df.index)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Year'] = df['Date'].dt.year
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row

Wet_Ann_Prob_CVPSCgtBL90
0                    7.462687
1                    7.462687
2                    7.462687
3                    7.462687
4                    7.462687
..                        ...
595                  0.000000
596                  0.000000
597                  0.000000
598                  0.000000
599                  0.000000

[600 rows x 1 columns]

In [113]:
Dry_Ann_Prob_CVPSCgtBL90 = exceedance_metric(dry_df, "DEL_CVP_PSC_N", 0.90, "Dry_Ann_Prob_CVPSCgtBL90", "TAF")
Dry_Ann_Prob_CVPSCgtBL90

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Date'] = pd.to_datetime(df.index)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Year'] = df['Date'].dt.year
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row

Dry_Ann_Prob_CVPSCgtBL90
0                    6.666667
1                    6.666667
2                    4.444444
3                    8.888889
4                    2.222222
..                        ...
595                  0.000000
596                  0.000000
597                  0.000000
598                  0.000000
599                  0.000000

[600 rows x 1 columns]

##### Probability of CVP NOD ag contractors annual delivery above specified threshold - Ann_Prob_CVPAGNgtBL90

In [114]:
Ann_Prob_CVPAGNgtBL90 = exceedance_metric(df, "DEL_CVP_PAG_N", 0.90, "Ann_Prob_CVPAGNgtBL90", "TAF")
Ann_Prob_CVPAGNgtBL90

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Date'] = pd.to_datetime(df.index)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Year'] = df['Date'].dt.year
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row

Ann_Prob_CVPAGNgtBL90
0                 8.536585
1                 9.756098
2                 1.219512
3                 1.219512
4                 1.219512
..                     ...
595               0.000000
596               0.000000
597               0.000000
598               0.000000
599               0.000000

[600 rows x 1 columns]

In [115]:
Wet_Ann_Prob_CVPAGNgtBL90 = exceedance_metric(wet_df, "DEL_CVP_PAG_N", 0.90, "Wet_Ann_Prob_CVPAGNgtBL90", "TAF")
Wet_Ann_Prob_CVPAGNgtBL90

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Date'] = pd.to_datetime(df.index)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Year'] = df['Date'].dt.year
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row

Wet_Ann_Prob_CVPAGNgtBL90
0                     7.462687
1                     7.462687
2                     1.492537
3                     1.492537
4                     1.492537
..                         ...
595                   0.000000
596                   0.000000
597                   0.000000
598                   0.000000
599                   0.000000

[600 rows x 1 columns]

In [116]:
Dry_Ann_Prob_CVPAGNgtBL90 = exceedance_metric(dry_df, "DEL_CVP_PAG_N", 0.90, "Dry_Ann_Prob_CVPAGNgtBL90", "TAF")
Dry_Ann_Prob_CVPAGNgtBL90

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Date'] = pd.to_datetime(df.index)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Year'] = df['Date'].dt.year
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row

Dry_Ann_Prob_CVPAGNgtBL90
0                     6.666667
1                    13.333333
2                     2.222222
3                     0.000000
4                     0.000000
..                         ...
595                   0.000000
596                   0.000000
597                   0.000000
598                   0.000000
599                   0.000000

[600 rows x 1 columns]

##### Probability of CVP SOD ag contractors annual delivery above specified threshold - Ann_Prob_CVPAGSgtBL90

In [117]:
Ann_Prob_CVPAGSgtBL90 = exceedance_metric(df, "DEL_CVP_PAG_S", 0.90, "Ann_Prob_CVPAGSgtBL90", "TAF")
Ann_Prob_CVPAGSgtBL90

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Date'] = pd.to_datetime(df.index)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Year'] = df['Date'].dt.year
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row

Ann_Prob_CVPAGSgtBL90
0                 8.536585
1                15.853659
2                 7.317073
3                 1.219512
4                 0.000000
..                     ...
595               0.000000
596               0.000000
597               0.000000
598               0.000000
599               0.000000

[600 rows x 1 columns]

In [118]:
Wet_Ann_Prob_CVPAGSgtBL90 = exceedance_metric(wet_df, "DEL_CVP_PAG_S", 0.90, "Wet_Ann_Prob_CVPAGSgtBL90", "TAF")
Wet_Ann_Prob_CVPAGSgtBL90

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Date'] = pd.to_datetime(df.index)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Year'] = df['Date'].dt.year
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row

Wet_Ann_Prob_CVPAGSgtBL90
0                     7.462687
1                    17.910448
2                     8.955224
3                     0.000000
4                     0.000000
..                         ...
595                   0.000000
596                   0.000000
597                   0.000000
598                   0.000000
599                   0.000000

[600 rows x 1 columns]

In [119]:
Dry_Ann_Prob_CVPAGSgtBL90 = exceedance_metric(dry_df, "DEL_CVP_PAG_S", 0.90, "Dry_Ann_Prob_CVPAGSgtBL90", "TAF")
Dry_Ann_Prob_CVPAGSgtBL90

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Date'] = pd.to_datetime(df.index)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Year'] = df['Date'].dt.year
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row

Dry_Ann_Prob_CVPAGSgtBL90
0                     6.666667
1                    22.222222
2                    15.555556
3                     2.222222
4                     0.000000
..                         ...
595                  15.555556
596                  15.555556
597                  15.555556
598                  15.555556
599                  13.333333

[600 rows x 1 columns]

##### Probability of CVP SOD Refuge annual deliveries above specified threshold - Ann_Prob_CVPRFSgtBL90

In [120]:
Ann_Prob_CVPRFSgtBL90 = exceedance_metric(df, "DEL_CVP_PRF_S", 0.90, "Ann_Prob_CVPRFSgtBL90", "TAF")
Ann_Prob_CVPRFSgtBL90

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Date'] = pd.to_datetime(df.index)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Year'] = df['Date'].dt.year
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row

Ann_Prob_CVPRFSgtBL90
0                 0.000000
1                 0.000000
2                 0.000000
3                 0.000000
4                 0.000000
..                     ...
595              64.634146
596              65.853659
597              65.853659
598              65.853659
599              65.853659

[600 rows x 1 columns]

In [121]:
Wet_Ann_Prob_CVPRFSgtBL90 = exceedance_metric(wet_df, "DEL_CVP_PRF_S", 0.90, "Wet_Ann_Prob_CVPRFSgtBL90", "TAF")
Wet_Ann_Prob_CVPRFSgtBL90

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Date'] = pd.to_datetime(df.index)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Year'] = df['Date'].dt.year
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row

Wet_Ann_Prob_CVPRFSgtBL90
0                     0.000000
1                     0.000000
2                     0.000000
3                     0.000000
4                     0.000000
..                         ...
595                  55.223881
596                  55.223881
597                  55.223881
598                  55.223881
599                  55.223881

[600 rows x 1 columns]

In [122]:
Dry_Ann_Prob_CVPRFSgtBL90 = exceedance_metric(dry_df, "DEL_CVP_PRF_S", 0.90, "Dry_Ann_Prob_CVPRFSgtBL90", "TAF")
Dry_Ann_Prob_CVPRFSgtBL90

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Date'] = pd.to_datetime(df.index)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Year'] = df['Date'].dt.year
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row

Dry_Ann_Prob_CVPRFSgtBL90
0                     0.000000
1                     0.000000
2                     0.000000
3                     0.000000
4                     0.000000
..                         ...
595                   2.222222
596                   2.222222
597                   2.222222
598                   2.222222
599                   2.222222

[600 rows x 1 columns]

### Frequency of hitting storage zone levels

In [123]:
def frequency_hitting_level(df, var_res, var_fldzn, units, vartitle, floodzone = True, months = None):
    subset_df_res = create_subset_unit(df, var_res, units)
    subset_df_floodzone = create_subset_unit(df, var_fldzn, units)
    
    if months is not None:
        subset_df_res = subset_df_res[subset_df_res.index.month.isin(months)]
        subset_df_floodzone = subset_df_floodzone[subset_df_floodzone.index.month.isin(months)]

    multiindex_columns = subset_df_res.columns

    subset_df_res_comp_values = subset_df_res.values - subset_df_floodzone.values
    if floodzone:
        subset_df_res_comp_values += 0.000001
        
    subset_df_res_comp = pd.DataFrame(subset_df_res_comp_values, index=subset_df_res.index, columns=multiindex_columns)
   
    exceedance_days = count_exceedance_days(subset_df_res_comp, 0)
    exceedance_days = exceedance_days / len(subset_df_res_comp) * 100
    if not floodzone: 
        exceedance_days = 100 - exceedance_days
    
    
    exceedance_days = exceedance_days.melt(value_name=vartitle).reset_index(drop=True)[[vartitle]]
    
    return exceedance_days

##### Floodzone

##### All_Prob_SHSTAflood

In [124]:
All_Prob_SHSTAflood = frequency_hitting_level(df, "S_SHSTA_", "S_SHSTALEVEL5DV", "TAF", "All_Prob_SHSTAflood")
All_Prob_SHSTAflood

All_Prob_SHSTAflood
0              31.707317
1              30.284553
2               8.943089
3               0.711382
4               0.000000
..                   ...
595            53.861789
596            58.434959
597            41.869919
598            24.085366
599             4.674797

[600 rows x 1 columns]

In [125]:
Wet_All_Prob_SHSTAflood = frequency_hitting_level(wet_df, "S_SHSTA_", "S_SHSTALEVEL5DV", "TAF", "Wet_All_Prob_SHSTAflood")
Wet_All_Prob_SHSTAflood

Wet_All_Prob_SHSTAflood
0                  47.435897
1                  44.070513
2                  12.980769
3                   1.121795
4                   0.000000
..                       ...
595                72.435897
596                71.474359
597                50.961538
598                28.205128
599                 6.730769

[600 rows x 1 columns]

In [126]:
Dry_All_Prob_SHSTAflood = frequency_hitting_level(dry_df, "S_SHSTA_", "S_SHSTALEVEL5DV", "TAF", "Dry_All_Prob_SHSTAflood")
Dry_All_Prob_SHSTAflood

Dry_All_Prob_SHSTAflood
0                   4.444444
1                   6.388889
2                   1.944444
3                   0.000000
4                   0.000000
..                       ...
595                21.666667
596                35.833333
597                26.111111
598                16.944444
599                 1.111111

[600 rows x 1 columns]

### Dead pool

##### Probability that end-of-September reservoir storage will be at dead pool (bottom of usable storage) - Sep_Prob_SHSTAdead; Sep_Prob_OROVLdead; Sep_Prob_TRNTYdead; Sep_Prob_MELONdead; Sep_Prob_MLRTNdead

##### Sep_Prob_SHSTAdead

In [127]:
Sep_Prob_SHSTAdead = frequency_hitting_level(df, "S_SHSTA_", "S_SHSTALEVEL1DV", "TAF", "Sep_Prob_SHSTAdead", floodzone=False, months=[9])
Sep_Prob_SHSTAdead

Sep_Prob_SHSTAdead
0              0.000000
1              0.000000
2              1.219512
3              6.097561
4             28.048780
..                  ...
595            0.000000
596            0.000000
597            0.000000
598            0.000000
599            0.000000

[600 rows x 1 columns]

In [128]:
Wet_Sep_Prob_SHSTAdead = frequency_hitting_level(wet_df, "S_SHSTA_", "S_SHSTALEVEL1DV", "TAF", "Wet_Sep_Prob_SHSTAdead", floodzone=False, months=[9])
Wet_Sep_Prob_SHSTAdead

Wet_Sep_Prob_SHSTAdead
0                  0.000000
1                  0.000000
2                  0.000000
3                  0.000000
4                 13.461538
..                      ...
595                0.000000
596                0.000000
597                0.000000
598                0.000000
599                0.000000

[600 rows x 1 columns]

In [129]:
Dry_Sep_Prob_SHSTAdead = frequency_hitting_level(dry_df, "S_SHSTA_", "S_SHSTALEVEL1DV", "TAF", "Dry_Sep_Prob_SHSTAdead", floodzone=False, months=[9])
Dry_Sep_Prob_SHSTAdead

Dry_Sep_Prob_SHSTAdead
0                  0.000000
1                  0.000000
2                  3.333333
3                 16.666667
4                 53.333333
..                      ...
595                0.000000
596                0.000000
597                0.000000
598                0.000000
599                0.000000

[600 rows x 1 columns]

##### Sep_Prob_OROVLdead

In [130]:
Sep_Prob_OROVLdead = frequency_hitting_level(df, "S_OROVL_", "S_OROVLLEVEL1DV", "TAF", "Sep_Prob_OROVLdead", floodzone=False, months=[9])
Sep_Prob_OROVLdead

Sep_Prob_OROVLdead
0              0.000000
1              0.000000
2              1.219512
3              4.878049
4             13.414634
..                  ...
595            0.000000
596            0.000000
597            0.000000
598            0.000000
599            0.000000

[600 rows x 1 columns]

In [131]:
Wet_Sep_Prob_OROVLdead = frequency_hitting_level(wet_df, "S_OROVL_", "S_OROVLLEVEL1DV", "TAF", "Wet_Sep_Prob_OROVLdead", floodzone=False, months=[9])
Wet_Sep_Prob_OROVLdead

Wet_Sep_Prob_OROVLdead
0                       0.0
1                       0.0
2                       0.0
3                       0.0
4                       0.0
..                      ...
595                     0.0
596                     0.0
597                     0.0
598                     0.0
599                     0.0

[600 rows x 1 columns]

In [132]:
Dry_Sep_Prob_OROVLdead = frequency_hitting_level(dry_df, "S_OROVL_", "S_OROVLLEVEL1DV", "TAF", "Dry_Sep_Prob_OROVLdead", floodzone=False, months=[9])
Dry_Sep_Prob_OROVLdead

Dry_Sep_Prob_OROVLdead
0                  0.000000
1                  0.000000
2                  3.333333
3                 13.333333
4                 36.666667
..                      ...
595                0.000000
596                0.000000
597                0.000000
598                0.000000
599                0.000000

[600 rows x 1 columns]

##### Sep_Prob_TRNTYdead

In [133]:
Sep_Prob_TRNTYdead = frequency_hitting_level(df, "S_TRNTY_", "S_TRNTYLEVEL1DV", "TAF", "Sep_Prob_TRNTYdead", floodzone=False, months=[9])
Sep_Prob_TRNTYdead

Sep_Prob_TRNTYdead
0              0.000000
1              0.000000
2              1.219512
3              7.317073
4             28.048780
..                  ...
595            0.000000
596            0.000000
597            0.000000
598            0.000000
599            0.000000

[600 rows x 1 columns]

In [134]:
Wet_Sep_Prob_TRNTYdead = frequency_hitting_level(wet_df, "S_TRNTY_", "S_TRNTYLEVEL1DV", "TAF", "Wet_Sep_Prob_TRNTYdead", floodzone=False, months=[9])
Wet_Sep_Prob_TRNTYdead

Wet_Sep_Prob_TRNTYdead
0                  0.000000
1                  0.000000
2                  0.000000
3                  1.923077
4                 13.461538
..                      ...
595                0.000000
596                0.000000
597                0.000000
598                0.000000
599                0.000000

[600 rows x 1 columns]

In [135]:
Dry_Sep_Prob_TRNTYdead = frequency_hitting_level(dry_df, "S_TRNTY_", "S_TRNTYLEVEL1DV", "TAF", "Dry_Sep_Prob_TRNTYdead", floodzone=False, months=[9])
Dry_Sep_Prob_TRNTYdead

Dry_Sep_Prob_TRNTYdead
0                  0.000000
1                  0.000000
2                  3.333333
3                 16.666667
4                 53.333333
..                      ...
595                0.000000
596                0.000000
597                0.000000
598                0.000000
599                0.000000

[600 rows x 1 columns]

##### Sep_Prob_MELONdead

In [136]:
Sep_Prob_MELONdead = frequency_hitting_level(df, "S_MELON_", "S_MELONLEVEL1DV", "TAF", "Sep_Prob_MELONdead", floodzone=False, months=[9])
Sep_Prob_MELONdead

Sep_Prob_MELONdead
0              2.439024
1              8.536585
2             34.146341
3             37.804878
4             45.121951
..                  ...
595            0.000000
596            0.000000
597            9.756098
598           20.731707
599           30.487805

[600 rows x 1 columns]

In [137]:
Wet_Sep_Prob_MELONdead = frequency_hitting_level(wet_df, "S_MELON_", "S_MELONLEVEL1DV", "TAF", "Wet_Sep_Prob_MELONdead", floodzone=False, months=[9])
Wet_Sep_Prob_MELONdead

Wet_Sep_Prob_MELONdead
0                  0.000000
1                  0.000000
2                 11.538462
3                 11.538462
4                 19.230769
..                      ...
595                0.000000
596                0.000000
597                0.000000
598                0.000000
599                5.769231

[600 rows x 1 columns]

In [138]:
Dry_Sep_Prob_MELONdead = frequency_hitting_level(dry_df, "S_MELON_", "S_MELONLEVEL1DV", "TAF", "Dry_Sep_Prob_MELONdead", floodzone=False, months=[9])
Dry_Sep_Prob_MELONdead

Dry_Sep_Prob_MELONdead
0                  6.666667
1                 23.333333
2                 73.333333
3                 83.333333
4                 90.000000
..                      ...
595                0.000000
596                0.000000
597               26.666667
598               56.666667
599               73.333333

[600 rows x 1 columns]

##### Sep_Prob_MLRTNdead

In [139]:
Sep_Prob_MLRTNdead = frequency_hitting_level(df, "S_MLRTN_", "S_MLRTNLEVEL1DV", "TAF", "Sep_Prob_MLRTNdead", floodzone=False, months=[9])
Sep_Prob_MLRTNdead

Sep_Prob_MLRTNdead
0              0.000000
1             78.048780
2             85.365854
3             84.146341
4             82.926829
..                  ...
595            0.000000
596           68.292683
597           70.731707
598           69.512195
599           69.512195

[600 rows x 1 columns]

In [140]:
Wet_Sep_Prob_MLRTNdead = frequency_hitting_level(wet_df, "S_MLRTN_", "S_MLRTNLEVEL1DV", "TAF", "Wet_Sep_Prob_MLRTNdead", floodzone=False, months=[9])
Wet_Sep_Prob_MLRTNdead

Wet_Sep_Prob_MLRTNdead
0                  0.000000
1                 84.615385
2                 96.153846
3                 96.153846
4                 96.153846
..                      ...
595                0.000000
596               82.692308
597               94.230769
598               92.307692
599               92.307692

[600 rows x 1 columns]

In [141]:
Dry_Sep_Prob_MLRTNdead = frequency_hitting_level(dry_df, "S_MLRTN_", "S_MLRTNLEVEL1DV", "TAF", "Dry_Sep_Prob_MLRTNdead", floodzone=False, months=[9])
Dry_Sep_Prob_MLRTNdead

Dry_Sep_Prob_MLRTNdead
0                  0.000000
1                 66.666667
2                 66.666667
3                 63.333333
4                 60.000000
..                      ...
595                0.000000
596               43.333333
597               30.000000
598               30.000000
599               30.000000

[600 rows x 1 columns]

##### More Standard Deviations

In [142]:
Std_Ann_Avg_SWPTotDel_TAF_df = compute_sd(df, "DEL_SWP_TOTAL", "TAF", "Std_Ann_Avg_SWPTotDel_TAF", months=None)
Std_Ann_Avg_SWPTotDel_TAF_df

Std_Ann_Avg_SWPTotDel_TAF
0                   176.410351
1                   179.342985
2                   182.498496
3                   182.995846
4                   178.929663
..                         ...
595                 161.315785
596                 162.689244
597                 163.525361
598                 163.374907
599                 155.788626

[600 rows x 1 columns]

In [143]:
Wet_Std_Ann_Avg_SWPTotDel_TAF_df = compute_sd(wet_df, "DEL_SWP_TOTAL", "TAF", "Wet_Std_Ann_Avg_SWPTotDel_TAF", months=None)
Wet_Std_Ann_Avg_SWPTotDel_TAF_df

Wet_Std_Ann_Avg_SWPTotDel_TAF
0                       180.090763
1                       183.519740
2                       188.331137
3                       191.557913
4                       189.916837
..                             ...
595                     164.289427
596                     165.378850
597                     167.514100
598                     168.877826
599                     163.901255

[600 rows x 1 columns]

In [144]:
Dry_Std_Ann_Avg_SWPTotDel_TAF_df = compute_sd(dry_df, "DEL_SWP_TOTAL", "TAF", "Dry_Std_Ann_Avg_SWPTotDel_TAF", months=None)
Dry_Std_Ann_Avg_SWPTotDel_TAF_df

Dry_Std_Ann_Avg_SWPTotDel_TAF
0                       142.179663
1                       142.215862
2                       136.064858
3                       135.579672
4                       133.386299
..                             ...
595                     147.641032
596                     149.523962
597                     142.652016
598                     131.897049
599                     121.812525

[600 rows x 1 columns]

In [145]:
Std_Ann_Avg_CVPSCEXDel_TAF_df = compute_sd(df, "DEL_CVP_PSCEX_TOTAL", "TAF", "Std_Ann_Avg_CVPSCEXDel_TAF", months=None)
Std_Ann_Avg_CVPSCEXDel_TAF_df

Std_Ann_Avg_CVPSCEXDel_TAF
0                    189.261445
1                    189.250752
2                    189.231041
3                    188.971424
4                    187.720478
..                          ...
595                  114.328310
596                  114.350763
597                  114.526992
598                  114.132582
599                  111.739250

[600 rows x 1 columns]

In [146]:
Wet_Std_Ann_Avg_CVPSCEXDel_TAF_df = compute_sd(wet_df, "DEL_CVP_PSCEX_TOTAL", "TAF", "Wet_Std_Ann_Avg_CVPSCEXDel_TAF", months=None)
Wet_Std_Ann_Avg_CVPSCEXDel_TAF_df

Wet_Std_Ann_Avg_CVPSCEXDel_TAF
0                        192.885856
1                        192.878414
2                        192.895351
3                        192.889679
4                        192.429903
..                              ...
594                      114.617106
595                      115.872673
596                      115.702309
597                      116.084558
598                      115.879897

[599 rows x 1 columns]

In [147]:
Dry_Std_Ann_Avg_CVPSCEXDel_TAF_df = compute_sd(dry_df, "DEL_CVP_PSCEX_TOTAL", "TAF", "Dry_Std_Ann_Avg_CVPSCEXDel_TAF", months=None)
Dry_Std_Ann_Avg_CVPSCEXDel_TAF_df

Dry_Std_Ann_Avg_CVPSCEXDel_TAF
0                        182.958329
1                        182.941835
2                        182.844539
3                        181.990108
4                        178.743126
..                              ...
594                      103.200132
595                      111.743082
596                      112.118809
597                      111.916653
598                      111.179248

[599 rows x 1 columns]

In [148]:
Std_Ann_Avg_SWPMIDel_TAF_df = compute_sd(df, "DEL_SWP_PMI", "TAF", "Std_Ann_Avg_SWPMIDel_TAF", months=None)
Std_Ann_Avg_SWPMIDel_TAF_df

Std_Ann_Avg_SWPMIDel_TAF
0                   86.805315
1                   87.976871
2                   89.540762
3                   90.068597
4                   86.388171
..                        ...
595                 89.197137
596                 90.435543
597                 91.395791
598                 91.507860
599                 86.292818

[600 rows x 1 columns]

In [149]:
Wet_Std_Ann_Avg_SWPMIDel_TAF_df = compute_sd(wet_df, "DEL_SWP_PMI", "TAF", "Wet_Std_Ann_Avg_SWPMIDel_TAF", months=None)
Wet_Std_Ann_Avg_SWPMIDel_TAF_df

Wet_Std_Ann_Avg_SWPMIDel_TAF
0                       84.778508
1                       86.624698
2                       91.012934
3                       94.388321
4                       92.369096
..                            ...
595                     88.995360
596                     89.754409
597                     91.931084
598                     93.434899
599                     91.170156

[600 rows x 1 columns]

In [150]:
Dry_Std_Ann_Avg_SWPMIDel_TAF_df = compute_sd(dry_df, "DEL_SWP_PMI", "TAF", "Dry_Std_Ann_Avg_SWPMIDel_TAF", months=None)
Dry_Std_Ann_Avg_SWPMIDel_TAF_df

Dry_Std_Ann_Avg_SWPMIDel_TAF
0                       66.741903
1                       65.373479
2                       58.918440
3                       58.560798
4                       57.985077
..                            ...
595                     82.036424
596                     83.979093
597                     78.773887
598                     71.420321
599                     64.240514

[600 rows x 1 columns]

In [151]:
Std_Ann_Avg_CVPRefDel_TAF_df = compute_sd(df, "DEL_CVP_PRF_TOTAL", "TAF", "Std_Ann_Avg_CVPRefDel_TAF", months=None)
Std_Ann_Avg_CVPRefDel_TAF_df

Std_Ann_Avg_CVPRefDel_TAF
0                    23.127171
1                    23.133883
2                    23.168558
3                    23.132446
4                    22.871553
..                         ...
595                  22.868431
596                  22.881950
597                  23.026778
598                  22.840359
599                  22.606742

[600 rows x 1 columns]

In [152]:
Wet_Std_Ann_Avg_CVPRefDel_TAF_df = compute_sd(wet_df, "DEL_CVP_PRF_TOTAL", "TAF", "Wet_Std_Ann_Avg_CVPRefDel_TAF", months=None)
Wet_Std_Ann_Avg_CVPRefDel_TAF_df

Wet_Std_Ann_Avg_CVPRefDel_TAF
0                        23.615075
1                        23.647903
2                        23.676584
3                        23.675000
4                        23.624320
..                             ...
594                      22.927947
595                      23.072901
596                      23.100861
597                      23.203458
598                      23.227420

[599 rows x 1 columns]

In [153]:
Dry_Std_Ann_Avg_CVPRefDel_TAF_df = compute_sd(dry_df, "DEL_CVP_PRF_TOTAL", "TAF", "Dry_Std_Ann_Avg_CVPRefDel_TAF", months=None)
Dry_Std_Ann_Avg_CVPRefDel_TAF_df

Dry_Std_Ann_Avg_CVPRefDel_TAF
0                        22.206716
1                        22.163040
2                        22.203968
3                        22.079108
4                        21.346609
..                             ...
594                      21.534807
595                      22.507644
596                      22.493984
597                      22.735907
598                      22.149018

[599 rows x 1 columns]

In [154]:
Std_Ann_Avg_SWPAGDel_TAF_df = compute_sd(df, "DEL_SWP_PAG", "TAF", "Std_Ann_Avg_SWPAGDel_TAF", months=None)
Std_Ann_Avg_SWPAGDel_TAF_df

Std_Ann_Avg_SWPAGDel_TAF
0                   99.791609
1                  101.385993
2                  103.563691
3                  104.709083
4                  104.170250
..                        ...
595                 75.332428
596                 75.555949
597                 75.562018
598                 75.684870
599                 74.017656

[600 rows x 1 columns]

In [238]:
Wet_Std_Ann_Avg_SWPAGDel_TAF_df = compute_sd(wet_df, "DEL_SWP_PAG", "TAF", "Wet_Std_Sep_Ann_Avg_SWPAGDel_TAF", months=None)
Wet_Std_Ann_Avg_SWPAGDel_TAF_df

Wet_Std_Sep_Ann_Avg_SWPAGDel_TAF
0                          104.263269
1                          105.400942
2                          106.511520
3                          108.082328
4                          108.716105
..                                ...
595                         78.034548
596                         78.320856
597                         78.385141
598                         78.560376
599                         76.858875

[600 rows x 1 columns]

In [239]:
Dry_Std_Ann_Avg_SWPAGDel_TAF_df = compute_sd(dry_df, "DEL_SWP_PAG", "TAF", "Dry_Std_Sep_Ann_Avg_SWPAGDel_TAF", months=None)
Dry_Std_Ann_Avg_SWPAGDel_TAF_df

Dry_Std_Sep_Ann_Avg_SWPAGDel_TAF
0                           85.716054
1                           87.611161
2                           89.247799
3                           90.047536
4                           88.216305
..                                ...
595                         68.905617
596                         69.087271
597                         67.648085
598                         65.170309
599                         63.053042

[600 rows x 1 columns]

In [276]:
Std_Sep_Avg_NODstorage_TAF_df = compute_sd(df, "S_RESTOT_NOD", "TAF", "Std_Sep_Avg_NODstorage_TAF", months=[9])
Std_Sep_Avg_NODstorage_TAF_df

Std_Sep_Avg_NODstorage_TAF
0                   1716.254383
1                   1615.693981
2                   1822.007377
3                   1760.675075
4                   1401.679054
..                          ...
595                 1210.639361
596                 1070.549761
597                 1261.778837
598                 1264.324766
599                 1181.837995

[600 rows x 1 columns]

In [277]:
Wet_Std_Sep_Avg_NODstorage_TAF_df = compute_sd(wet_df, "S_RESTOT_NOD", "TAF", "Wet_Std_Sep_Avg_NODstorage_TAF", months=[9])
Wet_Std_Sep_Avg_NODstorage_TAF_df

Wet_Std_Sep_Avg_NODstorage_TAF
0                       1076.394976
1                        940.708336
2                       1157.181638
3                       1334.320403
4                       1328.209609
..                              ...
595                      412.852431
596                      472.107683
597                      809.376270
598                      907.039066
599                     1103.758469

[600 rows x 1 columns]

In [278]:
Dry_Std_Sep_Avg_NODstorage_TAF_df = compute_sd(dry_df, "S_RESTOT_NOD", "TAF", "Dry_Std_Sep_Avg_NODstorage_TAF", months=[9])
Dry_Std_Sep_Avg_NODstorage_TAF_df

Dry_Std_Sep_Avg_NODstorage_TAF
0                       1310.736814
1                       1299.638337
2                       1480.269723
3                       1238.639036
4                        628.369324
..                              ...
595                     1023.075609
596                      781.197028
597                      826.618772
598                      841.954019
599                      716.625450

[600 rows x 1 columns]

In [160]:
Std_Apr_Avg_NODstorage_TAF_df = compute_sd(df, "S_RESTOT_NOD", "TAF", "Std_Apr_Avg_NODstorage_TAF", months=[4])
Std_Apr_Avg_NODstorage_TAF_df

Std_Apr_Avg_NODstorage_TAF
0                   1682.672151
1                   1592.417170
2                   1850.537653
3                   1830.401178
4                   1622.863128
..                          ...
595                 1009.528756
596                  945.006049
597                 1170.417031
598                 1213.367251
599                 1127.359519

[600 rows x 1 columns]

In [161]:
Wet_Std_Apr_Avg_NODstorage_TAF_df = compute_sd(wet_df, "S_RESTOT_NOD", "TAF", "Wet_Std_Apr_Avg_NODstorage_TAF", months=[4])
Wet_Std_Apr_Avg_NODstorage_TAF_df

Wet_Std_Apr_Avg_NODstorage_TAF
0                        696.272150
1                        730.192853
2                       1233.958051
3                       1351.195128
4                       1420.267910
..                              ...
595                      302.807772
596                      353.967375
597                      777.219583
598                      916.494531
599                     1032.188976

[600 rows x 1 columns]

In [162]:
Dry_Std_Apr_Avg_NODstorage_TAF_df = compute_sd(dry_df, "S_RESTOT_NOD", "TAF", "Dry_Std_Apr_Avg_NODstorage_TAF", months=[4])
Dry_Std_Apr_Avg_NODstorage_TAF_df

Dry_Std_Apr_Avg_NODstorage_TAF
0                       1640.807625
1                       1526.906957
2                       1706.187301
3                       1560.863664
4                       1102.797508
..                              ...
595                     1273.591393
596                     1132.172760
597                     1234.151156
598                     1148.853454
599                      879.771368

[600 rows x 1 columns]

In [163]:
Std_Apr_Avg_ShstaStorage_TAF_df = compute_sd(df, "S_SHSTA_", "TAF", "Std_Apr_Avg_ShstaStorage_TAF", months=[4])
Std_Apr_Avg_ShstaStorage_TAF_df

Std_Apr_Avg_ShstaStorage_TAF
0                      606.960306
1                      504.492912
2                      823.027828
3                      788.881099
4                      579.666646
..                            ...
595                    314.718369
596                    277.655330
597                    576.612410
598                    737.899595
599                    771.114234

[600 rows x 1 columns]

In [164]:
Wet_Std_Apr_Avg_ShstaStorage_TAF_df = compute_sd(wet_df, "S_SHSTA_", "TAF", "Wet_Std_Apr_Avg_ShstaStorage_TAF", months=[4])
Wet_Std_Apr_Avg_ShstaStorage_TAF_df

Wet_Std_Apr_Avg_ShstaStorage_TAF
0                          248.410736
1                          277.181016
2                          799.475061
3                          777.246085
4                          586.000911
..                                ...
595                        157.961390
596                        229.424101
597                        676.998462
598                        859.419586
599                        869.286720

[600 rows x 1 columns]

In [165]:
Dry_Std_Apr_Avg_ShstaStorage_TAF_df = compute_sd(dry_df, "S_SHSTA_", "TAF", "Dry_Std_Apr_Avg_ShstaStorage_TAF", months=[4])
Dry_Std_Apr_Avg_ShstaStorage_TAF_df

Dry_Std_Apr_Avg_ShstaStorage_TAF
0                          756.807174
1                          636.778066
2                          846.490160
3                          794.185489
4                          553.071648
..                                ...
595                        423.716044
596                        331.098294
597                        332.769626
598                        360.858780
599                        449.421706

[600 rows x 1 columns]

In [166]:
Std_Apr_Avg_OrovlStorage_TAF_df = compute_sd(df, "S_OROVL_", "TAF", "Std_Apr_Avg_OrovlStorage_TAF", months=[4])
Std_Apr_Avg_OrovlStorage_TAF_df

Std_Apr_Avg_OrovlStorage_TAF
0                      664.994160
1                      742.111093
2                      906.114440
3                      962.052423
4                      918.655101
..                            ...
595                    418.376254
596                    483.745102
597                    702.088825
598                    874.181146
599                    905.975413

[600 rows x 1 columns]

In [167]:
Wet_Std_Apr_Avg_OrovlStorage_TAF_df = compute_sd(wet_df, "S_OROVL_", "TAF", "Wet_Std_Apr_Avg_OrovlStorage_TAF", months=[4])
Wet_Std_Apr_Avg_OrovlStorage_TAF_df

Wet_Std_Apr_Avg_OrovlStorage_TAF
0                          301.991662
1                          423.195822
2                          691.969721
3                          825.157490
4                          854.930513
..                                ...
595                        115.136969
596                        183.432297
597                        461.398605
598                        697.236092
599                        833.511089

[600 rows x 1 columns]

In [168]:
Dry_Std_Apr_Avg_OrovlStorage_TAF_df = compute_sd(dry_df, "S_OROVL_", "TAF", "Dry_Std_Apr_Avg_OrovlStorage_TAF", months=[4])
Dry_Std_Apr_Avg_OrovlStorage_TAF_df

Dry_Std_Apr_Avg_OrovlStorage_TAF
0                          496.137603
1                          515.071978
2                          488.939535
3                          513.323966
4                          452.793603
..                                ...
595                        543.949657
596                        592.028731
597                        725.451068
598                        712.424691
599                        602.112351

[600 rows x 1 columns]

In [169]:
Std_Ann_Avg_NDO_TAF_df = compute_sd(df, "NDO", "TAF", "Std_Ann_Avg_NDO_TAF", months=None)
Std_Ann_Avg_NDO_TAF_df

Std_Ann_Avg_NDO_TAF
0            1890.908545
1            1925.453446
2            2006.227622
3            2048.889402
4            2068.957940
..                   ...
595          2078.842819
596          2110.776029
597          2172.222799
598          2224.809267
599          2288.541239

[600 rows x 1 columns]

In [170]:
Wet_Std_Ann_Avg_NDO_TAF_df = compute_sd(wet_df, "NDO", "TAF", "Wet_Std_Ann_Avg_NDO_TAF", months=None)
Wet_Std_Ann_Avg_NDO_TAF_df

Wet_Std_Ann_Avg_NDO_TAF
0                2217.816975
1                2243.330007
2                2323.757143
3                2354.695219
4                2367.029533
..                       ...
595              2407.159136
596              2441.948751
597              2513.370706
598              2564.631966
599              2617.038717

[600 rows x 1 columns]

In [171]:
Dry_Std_Ann_Avg_NDO_TAF_df = compute_sd(dry_df, "NDO", "TAF", "Dry_Std_Ann_Avg_NDO_TAF", months=None)
Dry_Std_Ann_Avg_NDO_TAF_df

Dry_Std_Ann_Avg_NDO_TAF
0                 642.706617
1                 765.898881
2                 858.415499
3                 923.937989
4                 912.632670
..                       ...
595               809.439098
596               863.737813
597               933.560206
598               999.475552
599              1100.995614

[600 rows x 1 columns]

### Check calculation - does doing 3 months affect at all?

In [172]:
Std_Fall_Avg_X2_KM_df = compute_sd(df, "X2_PRV", "KM", "Std_Fall_Avg_X2_KM", months=[9, 10, 11])
Std_Fall_Avg_X2_KM_df

Std_Fall_Avg_X2_KM
0              6.096765
1              5.988632
2              5.551175
3              5.528672
4              5.677755
..                  ...
595            7.837870
596            7.735257
597            6.309561
598            5.670913
599            5.090948

[600 rows x 1 columns]

In [173]:
Wet_Std_Fall_Avg_X2_KM_df = compute_sd(wet_df, "X2_PRV", "KM", "Wet_Std_Fall_Avg_X2_KM", months=[9, 10, 11])
Wet_Std_Fall_Avg_X2_KM_df

Wet_Std_Fall_Avg_X2_KM
0                  5.245283
1                  5.050293
2                  4.718089
3                  4.842330
4                  4.959473
..                      ...
595                7.493671
596                7.597554
597                6.262325
598                5.865718
599                5.502859

[600 rows x 1 columns]

In [174]:
Dry_Std_Fall_Avg_X2_KM_df = compute_sd(dry_df, "X2_PRV", "KM", "Dry_Std_Fall_Avg_X2_KM", months=[9, 10, 11])
Dry_Std_Fall_Avg_X2_KM_df

Dry_Std_Fall_Avg_X2_KM
0                  1.820721
1                  1.965529
2                  1.981834
3                  1.939197
4                  2.080009
..                      ...
595                3.643702
596                3.721425
597                3.596381
598                2.818564
599                2.174905

[600 rows x 1 columns]

In [175]:
Std_Spring_Avg_X2_KM_df = compute_sd(df, "X2_PRV", "KM", "Std_Spring_Avg_X2_KM", months=[3, 4, 5])
Std_Spring_Avg_X2_KM_df

Std_Spring_Avg_X2_KM
0               10.933313
1               10.803138
2               10.199386
3                9.926811
4                9.728437
..                    ...
595             11.117947
596             10.412075
597              9.698664
598              9.500892
599              9.179082

[600 rows x 1 columns]

In [176]:
Wet_Std_Spring_Avg_X2_KM_df = compute_sd(wet_df, "X2_PRV", "KM", "Wet_Std_Spring_Avg_X2_KM", months=[3, 4, 5])
Wet_Std_Spring_Avg_X2_KM_df

Wet_Std_Spring_Avg_X2_KM
0                    7.387655
1                    7.056599
2                    6.326248
3                    5.876811
4                    5.353493
..                        ...
595                  6.767225
596                  6.470920
597                  5.842730
598                  5.311938
599                  4.828986

[600 rows x 1 columns]

In [177]:
Dry_Std_Spring_Avg_X2_KM_df = compute_sd(dry_df, "X2_PRV", "KM", "Dry_Std_Spring_Avg_X2_KM", months=[3, 4, 5])
Dry_Std_Spring_Avg_X2_KM_df

Dry_Std_Spring_Avg_X2_KM
0                    7.640112
1                    8.134872
2                    8.363255
3                    8.493483
4                    8.739121
..                        ...
595                  9.059136
596                  8.720433
597                  8.582877
598                  8.935210
599                  9.010487

[600 rows x 1 columns]

In [178]:
Std_Ann_Avg_CVPTotDel_TAF_df = compute_sd(df_cvptot, "DEL_CVP_TOTAL", "TAF", "Std_Ann_Avg_CVPTotDel_TAF", months=None)
Std_Ann_Avg_CVPTotDel_TAF_df

Std_Ann_Avg_CVPTotDel_TAF
0                   184.615821
1                   133.820212
2                   310.451277
3                   185.061047
4                   142.560151
..                         ...
595                 133.132821
596                 296.303957
597                 141.639744
598                 123.947146
599                 261.543087

[600 rows x 1 columns]

In [179]:
Wet_Std_Ann_Avg_CVPTotDel_TAF_df = compute_sd(wet_df_cvptot, "DEL_CVP_TOTAL", "TAF", "Wet_Std_Ann_Avg_CVPTotDel_TAF", months=None)
Wet_Std_Ann_Avg_CVPTotDel_TAF_df

Wet_Std_Ann_Avg_CVPTotDel_TAF
0                       192.635626
1                       143.996791
2                       331.721736
3                       192.963298
4                       151.957876
..                             ...
595                     139.294120
596                     311.504827
597                     152.198784
598                     130.747059
599                     279.183179

[600 rows x 1 columns]

In [180]:
Dry_Std_Ann_Avg_CVPTotDel_TAF_df = compute_sd(dry_df_cvptot, "DEL_CVP_TOTAL", "TAF", "Dry_Std_Ann_Avg_CVPTotDel_TAF", months=None)
Dry_Std_Ann_Avg_CVPTotDel_TAF_df

Dry_Std_Ann_Avg_CVPTotDel_TAF
0                       169.317564
1                        97.884898
2                       259.458488
3                       170.040685
4                       111.238478
..                             ...
595                     116.972776
596                     262.473490
597                     118.763571
598                     105.545854
599                     219.939587

[600 rows x 1 columns]

In [181]:
Std_Ann_Avg_CVPAgDel_TAF_df = compute_sd(df, "DEL_CVP_PAG_TOTAL", "TAF", "Std_Ann_Avg_CVPAgDel_TAF", months=None)
Std_Ann_Avg_CVPAgDel_TAF_df

Std_Ann_Avg_CVPAgDel_TAF
0                  114.074101
1                  122.678115
2                  115.269486
3                   89.963916
4                   54.436733
..                        ...
595                 80.549475
596                 80.691609
597                 80.688902
598                 80.570814
599                 79.226336

[600 rows x 1 columns]

In [182]:
Wet_Std_Ann_Avg_CVPAgDel_TAF_df = compute_sd(wet_df, "DEL_CVP_PAG_TOTAL", "TAF", "Wet_Std_Ann_Avg_CVPAgDel_TAF", months=None)
Wet_Std_Ann_Avg_CVPAgDel_TAF_df

Wet_Std_Ann_Avg_CVPAgDel_TAF
0                      123.359631
1                      131.757336
2                      124.741942
3                      101.138562
4                       61.412725
..                            ...
595                     81.887944
596                     81.873799
597                     81.870878
598                     81.842681
599                     81.540376

[600 rows x 1 columns]

In [183]:
Dry_Std_Ann_Avg_CVPAgDel_TAF_df = compute_sd(dry_df, "DEL_CVP_PAG_TOTAL", "TAF", "Dry_Std_Ann_Avg_CVPAgDel_TAF", months=None)
Dry_Std_Ann_Avg_CVPAgDel_TAF_df

Dry_Std_Ann_Avg_CVPAgDel_TAF
0                       72.193953
1                       85.975738
2                       80.574462
3                       55.538729
4                       37.507912
..                            ...
595                     78.198014
596                     78.642155
597                     78.640093
598                     78.341831
599                     74.784163

[600 rows x 1 columns]

In [184]:
Std_Ann_Avg_BanksJones_TAF_df = compute_sd(df, "D_TOTAL", "TAF", "Std_Ann_Avg_BanksJones_TAF", months=None)
Std_Ann_Avg_BanksJones_TAF_df

Std_Ann_Avg_BanksJones_TAF
0                    172.760553
1                    165.204098
2                    173.604881
3                    178.683033
4                    182.682749
..                          ...
595                  166.627960
596                  157.971081
597                  149.202704
598                  147.609958
599                  146.020973

[600 rows x 1 columns]

In [185]:
Wet_Std_Ann_Avg_BanksJones_TAF_df = compute_sd(wet_df, "D_TOTAL", "TAF", "Wet_Std_Ann_Avg_BanksJones_TAF", months=None)
Wet_Std_Ann_Avg_BanksJones_TAF_df

Wet_Std_Ann_Avg_BanksJones_TAF
0                        142.125454
1                        130.507941
2                        154.225905
3                        170.501238
4                        180.647097
..                              ...
595                      151.359067
596                      143.248091
597                      140.061208
598                      142.378915
599                      148.844858

[600 rows x 1 columns]

In [186]:
Dry_Std_Ann_Avg_BanksJones_TAF_df = compute_sd(dry_df, "D_TOTAL", "TAF", "Dry_Std_Ann_Avg_BanksJones_TAF", months=None)
Dry_Std_Ann_Avg_BanksJones_TAF_df

Dry_Std_Ann_Avg_BanksJones_TAF
0                        119.482756
1                        127.813269
2                        148.511576
3                        157.393602
4                        166.734112
..                              ...
595                      169.526626
596                      159.042099
597                      136.929279
598                      127.639860
599                      119.969554

[600 rows x 1 columns]

In [187]:
Std_Ann_Avg_SWPTotDel_TAF_df = compute_sd(df, "DEL_SWP_TOTAL", "TAF", "Std_Ann_Avg_SWPTotDel_TAF", months=None)
Std_Ann_Avg_SWPTotDel_TAF_df

Std_Ann_Avg_SWPTotDel_TAF
0                   176.410351
1                   179.342985
2                   182.498496
3                   182.995846
4                   178.929663
..                         ...
595                 161.315785
596                 162.689244
597                 163.525361
598                 163.374907
599                 155.788626

[600 rows x 1 columns]

In [188]:
Wet_Std_Ann_Avg_SWPTotDel_TAF_df = compute_sd(wet_df, "DEL_SWP_TOTAL", "TAF", "Wet_Std_Ann_Avg_SWPTotDel_TAF", months=None)
Wet_Std_Ann_Avg_SWPTotDel_TAF_df

Wet_Std_Ann_Avg_SWPTotDel_TAF
0                       180.090763
1                       183.519740
2                       188.331137
3                       191.557913
4                       189.916837
..                             ...
595                     164.289427
596                     165.378850
597                     167.514100
598                     168.877826
599                     163.901255

[600 rows x 1 columns]

In [189]:
Dry_Std_Ann_Avg_SWPTotDel_TAF_df = compute_sd(dry_df, "DEL_SWP_TOTAL", "TAF", "Dry_Std_Ann_Avg_SWPTotDel_TAF", months=None)
Dry_Std_Ann_Avg_SWPTotDel_TAF_df

Dry_Std_Ann_Avg_SWPTotDel_TAF
0                       142.179663
1                       142.215862
2                       136.064858
3                       135.579672
4                       133.386299
..                             ...
595                     147.641032
596                     149.523962
597                     142.652016
598                     131.897049
599                     121.812525

[600 rows x 1 columns]

#### Ann_Avg_CVPSWPTotDel_TAF

In [190]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(df, "DEL_CVPSWP_TOTAL", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Ann_Avg_CVPSWPTotDel_TAF_df = pd.DataFrame(metrics, columns=['Ann_Avg_CVPSWPTotDel_TAF'])
Ann_Avg_CVPSWPTotDel_TAF_df

Ann_Avg_CVPSWPTotDel_TAF
0                 8265.886088
1                 8486.134966
2                 8140.591856
3                 7517.455768
4                 6905.624174
..                        ...
379               6575.831503
380               7593.890249
381               7702.441398
382               7568.776541
383               7267.038079

[384 rows x 1 columns]

In [222]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(wet_df, "DEL_CVPSWP_TOTAL", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Wet_Ann_Avg_CVPSWPTotDel_TAF_df = pd.DataFrame(metrics, columns=['Wet_Ann_Avg_CVPSWPTotDel_TAF'])
Wet_Ann_Avg_CVPSWPTotDel_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Wet_Ann_Avg_CVPSWPTotDel_TAF
0                     7134.695122
1                     7309.199094
2                     7050.292857
3                     6474.400071
4                     5873.834295
..                            ...
379                   5554.830085
380                   6343.403924
381                   6396.799799
382                   6369.898382
383                   6210.504380

[384 rows x 1 columns]

In [192]:
metrics = []

for study_index in np.arange(0, len(dss_names)):
    metric_value = compute_mean(dry_df, "DEL_CVPSWP_TOTAL", [study_index], "TAF", months=None)
    metrics.append(metric_value)

Dry_Ann_Avg_CVPSWPTotDel_TAF_df = pd.DataFrame(metrics, columns=['Dry_Ann_Avg_CVPSWPTotDel_TAF'])
Dry_Ann_Avg_CVPSWPTotDel_TAF_df

/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv452zz42274h4l4zb4h0000gn/T/ipykernel_35621/12486618.py:6: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  return df.drop(["Date", "Year", "Month"], axis = 1)
/var/folders/p6/z8ptzv45

Dry_Ann_Avg_CVPSWPTotDel_TAF
0                     4439.513024
1                     4581.038398
2                     4336.864684
3                     4058.812627
4                     3838.095211
..                            ...
379                   3712.101501
380                   4393.131944
381                   4511.435737
382                   4307.921883
383                   3995.407311

[384 rows x 1 columns]

In [261]:
Std_Ann_Avg_CVPSWPTotDel_TAF_df = compute_sd(df, "DEL_CVPSWP_TOTAL", "TAF", "Std_Ann_Avg_CVPSWPTotDel_TAF",months=None)
Wet_Std_Ann_Avg_CVPSWPTotDel_TAF_df = compute_sd(wet_df, "DEL_CVPSWP_TOTAL", "TAF", "Wet_Std_Ann_Avg_CVPSWPTotDel_TAF", months=None)
Dry_Std_Ann_Avg_CVPSWPTotDel_TAF_df = compute_sd(dry_df, "DEL_CVPSWP_TOTAL", "TAF", "Dry_Std_Ann_Avg_CVPSWPTotDel_TAF", months=None)

#### more del-cvp's (not used)

In [194]:
# metrics = []

# for study_index in np.arange(0, len(dss_names)):
#     metric_value = compute_mean(df, ["DEL_CVP_PAG_N"], [study_index], months=None)
#     metrics.append(metric_value)

# pag_n_results_df = pd.DataFrame(metrics, columns=['NOD AG Delivery Mean (TAF)'])
# pag_n_results_df

In [195]:
# wet_metrics = []

# for study_index in np.arange(0, len(dss_names)):
#     metric_value = compute_mean(wet_df, ["DEL_CVP_PAG_N"], [study_index], months=None)
#     wet_metrics.append(metric_value)

# wet_pag_n_results_df = pd.DataFrame(wet_metrics, columns=['Wet NOD AG Delivery Mean (TAF)'])
# wet_pag_n_results_df

In [196]:
# dry_metrics = []

# for study_index in np.arange(0, len(dss_names)):
#     metric_value = compute_mean(dry_df, ["DEL_CVP_PAG_N"], [study_index], months=None)
#     dry_metrics.append(metric_value)

# dry_pag_n_results_df = pd.DataFrame(dry_metrics, columns=['Dry NOD AG Delivery Mean (TAF)'])
# dry_pag_n_results_df

In [197]:
# metrics = []

# for study_index in np.arange(0, len(dss_names)):
#     metric_value = compute_mean(df, ["DEL_CVP_PAG_S"], [study_index], months=None)
#     metrics.append(metric_value)

# pag_s_results_df = pd.DataFrame(metrics, columns=['SOD AG Delivery Mean (TAF)'])
# pag_s_results_df

In [198]:
# wet_metrics = []

# for study_index in np.arange(0, len(dss_names)):
#     metric_value = compute_mean(wet_df, ["DEL_CVP_PAG_S"], [study_index], months=None)
#     wet_metrics.append(metric_value)

# wet_pag_s_results_df = pd.DataFrame(wet_metrics, columns=['Wet SOD AG Delivery Mean (TAF)'])
# wet_pag_s_results_df

In [199]:
# dry_metrics = []

# for study_index in np.arange(0, len(dss_names)):
#     metric_value = compute_mean(dry_df, ["DEL_CVP_PAG_S"], [study_index], months=None)
#     dry_metrics.append(metric_value)

# dry_pag_s_results_df = pd.DataFrame(dry_metrics, columns=['Dry SOD AG Delivery Mean (TAF)'])
# dry_pag_s_results_df

In [200]:
# metrics = []

# for study_index in np.arange(0, len(dss_names)):
#     metric_value = compute_mean(df, ["DEL_CVP_PRF_S"], [study_index], months=None)
#     metrics.append(metric_value)

# prf_s_results_df = pd.DataFrame(metrics, columns=['SOD Refuge Delivery Mean (TAF)'])
# prf_s_results_df

In [201]:
# wet_metrics = []

# for study_index in np.arange(0, len(dss_names)):
#     metric_value = compute_mean(wet_df, ["DEL_CVP_PRF_S"], [study_index], months=None)
#     wet_metrics.append(metric_value)

# wet_prf_s_results_df = pd.DataFrame(wet_metrics, columns=['Wet SOD Refuge Delivery Mean (TAF)'])
# wet_prf_s_results_df

In [202]:
# dry_metrics = []

# for study_index in np.arange(0, len(dss_names)):
#     metric_value = compute_mean(dry_df, ["DEL_CVP_PRF_S"], [study_index], months=None)
#     dry_metrics.append(metric_value)

# dry_prf_s_results_df = pd.DataFrame(dry_metrics, columns=['Dry SOD Refuge Delivery Mean (TAF)'])
# dry_prf_s_results_df

#### total reservoirs (not used)

In [203]:
# metrics = []

# for study_index in np.arange(0, len(dss_names)):
#     metric_value = compute_mean(df, ["S_RESTOT"], [study_index], months=[4])
#     metrics.append(metric_value)

# stot_apr_results_df = pd.DataFrame(metrics, columns=['Reservoir Storage April Mean (TAF)'])
# stot_apr_results_df

In [204]:
# wet_metrics = []

# for study_index in np.arange(0, len(dss_names)):
#     metric_value = compute_mean(wet_df, ["S_RESTOT"], [study_index], months=[4])
#     wet_metrics.append(metric_value)

# wet_stot_apr_results_df = pd.DataFrame(wet_metrics, columns=['Wet Reservoir Storage April Mean (TAF)'])
# wet_stot_apr_results_df

In [205]:
# dry_metrics = []

# for study_index in np.arange(0, len(dss_names)):
#     metric_value = compute_mean(dry_df, ["S_RESTOT"], [study_index], months=[4])
#     dry_metrics.append(metric_value)

# dry_stot_apr_results_df = pd.DataFrame(dry_metrics, columns=['Dry Reservoir Storage April Mean (TAF)'])
# dry_stot_apr_results_df

#### Concatenate

In [223]:
knobs_params_equity = pd.read_csv(DataDir + "metrics_add_on.csv")
knobs_params_equity_unique = knobs_params_equity.iloc[:, 0:8]
knobs_params_equity_unique

Study    d    c  p  r    m    Equity  Ann_Avg_CVPAgUnmet
0    expl0000  1.0  1.0  0  1  0.0  0.714361            0.712650
1    expl0001  1.0  1.0  0  1  0.4  0.736049            0.742762
2    expl0002  1.0  1.0  0  1  0.6  0.690417            0.705558
3    expl0003  1.0  1.0  0  1  0.7  0.584353            0.612065
4    expl0004  1.0  1.0  0  1  0.8  0.479570            0.533874
..        ...  ...  ... .. ..  ...       ...                 ...
595  expl0595  0.6  1.2  1  4  0.0  0.845883            0.843323
596  expl0596  0.6  1.2  1  4  0.4  0.847116            0.844431
597  expl0597  0.6  1.2  1  4  0.6  0.838216            0.844700
598  expl0598  0.6  1.2  1  4  0.7  0.821299            0.842910
599  expl0599  0.6  1.2  1  4  0.8  0.791608            0.824738

[600 rows x 8 columns]

In [224]:
knobs_params_equity_unique_wet_dry = knobs_params_equity.iloc[:, 0:6]
knobs_params_equity_unique_wet_dry

Study    d    c  p  r    m
0    expl0000  1.0  1.0  0  1  0.0
1    expl0001  1.0  1.0  0  1  0.4
2    expl0002  1.0  1.0  0  1  0.6
3    expl0003  1.0  1.0  0  1  0.7
4    expl0004  1.0  1.0  0  1  0.8
..        ...  ...  ... .. ..  ...
595  expl0595  0.6  1.2  1  4  0.0
596  expl0596  0.6  1.2  1  4  0.4
597  expl0597  0.6  1.2  1  4  0.6
598  expl0598  0.6  1.2  1  4  0.7
599  expl0599  0.6  1.2  1  4  0.8

[600 rows x 6 columns]

In [279]:
all_non_sd_metrics = pd.concat([knobs_params_equity_unique, Ann_Avg_CVPSWPTotDel_TAF_df, Ann_Avg_SWPTotDel_TAF_df, Ann_Avg_CVPSCEXDel_TAF_df, Ann_Avg_SWPMIDel_TAF_df, Ann_Avg_CVPRefDel_TAF_df, Ann_Avg_SWPAGDel_TAF_df, Sep_Avg_NODstorage_TAF_df, Apr_Avg_NODstorage_TAF_df, Apr_Avg_ShstaStorage_TAF_df, Apr_Avg_OrovlStorage_TAF_df, Ann_Avg_NDO_TAF_df, Fall_Avg_X2_KM_df, Spring_Avg_X2_KM_df, Ann_Avg_CVPTotDel_TAF_df, Ann_Avg_CVPAgDel_TAF_df, Ann_Avg_BanksJones_TAF_df, Ann_Prob_CVPMINgtBL90, Ann_Prob_CVPMISgtBL90, Apr_Prob_SHSTAgt38, Ann_Prob_CVPSCgtBL90, Ann_Prob_CVPAGNgtBL90, Ann_Prob_CVPAGSgtBL90, Ann_Prob_CVPRFSgtBL90, Oct_StDev_X2, Apr_StDev_X2, All_Prob_SHSTAflood, Sep_Prob_SHSTAdead, Sep_Prob_OROVLdead, Sep_Prob_TRNTYdead, Sep_Prob_MELONdead, Sep_Prob_MLRTNdead], axis=1)
all_non_sd_metrics

Study    d    c  p  r    m    Equity  Ann_Avg_CVPAgUnmet  \
0    expl0000  1.0  1.0  0  1  0.0  0.714361            0.712650   
1    expl0001  1.0  1.0  0  1  0.4  0.736049            0.742762   
2    expl0002  1.0  1.0  0  1  0.6  0.690417            0.705558   
3    expl0003  1.0  1.0  0  1  0.7  0.584353            0.612065   
4    expl0004  1.0  1.0  0  1  0.8  0.479570            0.533874   
..        ...  ...  ... .. ..  ...       ...                 ...   
595  expl0595  0.6  1.2  1  4  0.0  0.845883            0.843323   
596  expl0596  0.6  1.2  1  4  0.4  0.847116            0.844431   
597  expl0597  0.6  1.2  1  4  0.6  0.838216            0.844700   
598  expl0598  0.6  1.2  1  4  0.7  0.821299            0.842910   
599  expl0599  0.6  1.2  1  4  0.8  0.791608            0.824738   

     Ann_Avg_CVPSWPTotDel_TAF  Ann_Avg_SWPTotDel_TAF  ...  \
0                 8265.886088            3450.959450  ...   
1                 8486.134966            3499.658107  ...   
2                 8140.591856            3373.532604  ...   
3                 7517.455768            3302.689714  ...   
4                 6905.624174            3170.088090  ...   
..                        ...                    ...  ...   
595                       NaN                    NaN  ...   
596                       NaN                    NaN  ...   
597                       NaN                    NaN  ...   
598                       NaN                    NaN  ...   
599                       NaN                    NaN  ...   

     Ann_Prob_CVPAGSgtBL90  Ann_Prob_CVPRFSgtBL90  Oct_StDev_X2  Apr_StDev_X2  \
0                 8.536585               0.000000      6.542445     10.346875   
1                15.853659               0.000000      6.414817     10.206163   
2                 7.317073               0.000000      5.933861      9.572897   
3                 1.219512               0.000000      5.909413      9.231497   
4                 0.000000               0.000000      5.926163      8.921624   
..                     ...                    ...           ...           ...   
595               0.000000              64.634146      8.176955     10.292074   
596               0.000000              65.853659      7.965440      9.747449   
597               0.000000              65.853659      5.983565      9.091666   
598               0.000000              65.853659      5.058976      8.797966   
599               0.000000              65.853659      4.241868      8.375252   

     All_Prob_SHSTAflood  Sep_Prob_SHSTAdead  Sep_Prob_OROVLdead  \
0              31.707317            0.000000            0.000000   
1              30.284553            0.000000            0.000000   
2               8.943089            1.219512            1.219512   
3               0.711382            6.097561            4.878049   
4               0.000000           28.048780           13.414634   
..                   ...                 ...                 ...   
595            53.861789            0.000000            0.000000   
596            58.434959            0.000000            0.000000   
597            41.869919            0.000000            0.000000   
598            24.085366            0.000000            0.000000   
599             4.674797            0.000000            0.000000   

     Sep_Prob_TRNTYdead  Sep_Prob_MELONdead  Sep_Prob_MLRTNdead  
0              0.000000            2.439024            0.000000  
1              0.000000            8.536585           78.048780  
2              1.219512           34.146341           85.365854  
3              7.317073           37.804878           84.146341  
4             28.048780           45.121951           82.926829  
..                  ...                 ...                 ...  
595            0.000000            0.000000            0.000000  
596            0.000000            0.000000           68.292683  
597            0.000000            9.756098           70.731707  
598     

In [280]:
all_sd_results = pd.concat([Std_Ann_Avg_CVPSWPTotDel_TAF_df, Std_Ann_Avg_SWPTotDel_TAF_df, Std_Ann_Avg_CVPSCEXDel_TAF_df, Std_Ann_Avg_SWPMIDel_TAF_df, Std_Ann_Avg_CVPRefDel_TAF_df, Std_Ann_Avg_SWPAGDel_TAF_df, Std_Sep_Avg_NODstorage_TAF_df, Std_Apr_Avg_NODstorage_TAF_df, Std_Apr_Avg_ShstaStorage_TAF_df, Std_Apr_Avg_OrovlStorage_TAF_df, Std_Ann_Avg_NDO_TAF_df, Std_Fall_Avg_X2_KM_df, Std_Spring_Avg_X2_KM_df, Std_Ann_Avg_CVPTotDel_TAF_df, Std_Ann_Avg_CVPAgDel_TAF_df, Std_Ann_Avg_BanksJones_TAF_df], axis = 1)
all_sd_results

Std_Ann_Avg_CVPSWPTotDel_TAF  Std_Ann_Avg_SWPTotDel_TAF  \
0                      459.372816                 176.410351   
1                      472.209085                 179.342985   
2                      464.263070                 182.498496   
3                      433.720363                 182.995846   
4                      400.843734                 178.929663   
..                            ...                        ...   
595                    331.173458                 161.315785   
596                    332.329449                 162.689244   
597                    332.492854                 163.525361   
598                    331.958025                 163.374907   
599                    322.673687                 155.788626   

     Std_Ann_Avg_CVPSCEXDel_TAF  Std_Ann_Avg_SWPMIDel_TAF  \
0                    189.261445                 86.805315   
1                    189.250752                 87.976871   
2                    189.231041                 89.540762   
3                    188.971424                 90.068597   
4                    187.720478                 86.388171   
..                          ...                       ...   
595                  114.328310                 89.197137   
596                  114.350763                 90.435543   
597                  114.526992                 91.395791   
598                  114.132582                 91.507860   
599                  111.739250                 86.292818   

     Std_Ann_Avg_CVPRefDel_TAF  Std_Ann_Avg_SWPAGDel_TAF  \
0                    23.127171                 99.791609   
1                    23.133883                101.385993   
2                    23.168558                103.563691   
3                    23.132446                104.709083   
4                    22.871553                104.170250   
..                         ...                       ...   
595                  22.868431                 75.332428   
596                  22.881950                 75.555949   
597                  23.026778                 75.562018   
598                  22.840359                 75.684870   
599                  22.606742                 74.017656   

     Std_Sep_Avg_NODstorage_TAF  Std_Apr_Avg_NODstorage_TAF  \
0                   1716.254383                 1682.672151   
1                   1615.693981                 1592.417170   
2                   1822.007377                 1850.537653   
3                   1760.675075                 1830.401178   
4                   1401.679054                 1622.863128   
..                          ...                         ...   
595                 1210.639361                 1009.528756   
596                 1070.549761                  945.006049   
597                 1261.778837                 1170.417031   
598                 1264.324766                 1213.367251   
599                 1181.837995                 1127.359519   

     Std_Apr_Avg_ShstaStorage_TAF  Std_Apr_Avg_OrovlStorage_TAF  \
0                      606.960306                    664.994160   
1                      504.492912                    742.111093   
2                      823.027828                    906.114440   
3                      788.881099                    962.052423   
4                      579.666646                    918.655101   
..                            ...                           ...   
595                    314.718369                    418.376254   
596                    277.655330                    483.745102   
597                    576.612410                    702.088825   
598                    737.899595                    874.181146   
599                    771.114234                    905.975413   

     Std_Ann_Avg_NDO_TAF  Std_Fall_Avg_X2_KM  Std_Spring_Avg_X2_KM  \
0            1890.908545            6.096765             10.933313   
1            1925.453446            5.988632             10.803138   
2         

In [281]:
all_results_df = pd.concat([knobs_params_equity_unique, Ann_Avg_CVPSWPTotDel_TAF_df, Std_Ann_Avg_CVPSWPTotDel_TAF_df, Ann_Avg_SWPTotDel_TAF_df, Std_Ann_Avg_SWPTotDel_TAF_df, Ann_Avg_CVPSCEXDel_TAF_df, Std_Ann_Avg_CVPSCEXDel_TAF_df, Ann_Avg_SWPMIDel_TAF_df, Std_Ann_Avg_SWPMIDel_TAF_df, Ann_Avg_CVPRefDel_TAF_df, Std_Ann_Avg_CVPRefDel_TAF_df, Ann_Avg_SWPAGDel_TAF_df, Std_Ann_Avg_SWPAGDel_TAF_df, Sep_Avg_NODstorage_TAF_df, Std_Sep_Avg_NODstorage_TAF_df, Apr_Avg_NODstorage_TAF_df, Std_Apr_Avg_NODstorage_TAF_df, Apr_Avg_ShstaStorage_TAF_df, Std_Apr_Avg_ShstaStorage_TAF_df, Apr_Avg_OrovlStorage_TAF_df, Std_Apr_Avg_OrovlStorage_TAF_df, Ann_Avg_NDO_TAF_df, Std_Ann_Avg_NDO_TAF_df, Fall_Avg_X2_KM_df, Std_Fall_Avg_X2_KM_df, Spring_Avg_X2_KM_df, Std_Spring_Avg_X2_KM_df, Ann_Avg_CVPTotDel_TAF_df, Std_Ann_Avg_CVPTotDel_TAF_df,  Ann_Avg_CVPAgDel_TAF_df, Std_Ann_Avg_CVPAgDel_TAF_df, Ann_Avg_BanksJones_TAF_df, Std_Ann_Avg_BanksJones_TAF_df, Ann_Prob_CVPMINgtBL90, Ann_Prob_CVPMISgtBL90, Apr_Prob_SHSTAgt38, Ann_Prob_CVPSCgtBL90, Ann_Prob_CVPAGNgtBL90, Ann_Prob_CVPAGSgtBL90, Ann_Prob_CVPRFSgtBL90, Oct_StDev_X2, Apr_StDev_X2, All_Prob_SHSTAflood, Sep_Prob_SHSTAdead, Sep_Prob_OROVLdead, Sep_Prob_TRNTYdead, Sep_Prob_MELONdead, Sep_Prob_MLRTNdead], axis=1)
all_results_df

Study    d    c  p  r    m    Equity  Ann_Avg_CVPAgUnmet  \
0    expl0000  1.0  1.0  0  1  0.0  0.714361            0.712650   
1    expl0001  1.0  1.0  0  1  0.4  0.736049            0.742762   
2    expl0002  1.0  1.0  0  1  0.6  0.690417            0.705558   
3    expl0003  1.0  1.0  0  1  0.7  0.584353            0.612065   
4    expl0004  1.0  1.0  0  1  0.8  0.479570            0.533874   
..        ...  ...  ... .. ..  ...       ...                 ...   
595  expl0595  0.6  1.2  1  4  0.0  0.845883            0.843323   
596  expl0596  0.6  1.2  1  4  0.4  0.847116            0.844431   
597  expl0597  0.6  1.2  1  4  0.6  0.838216            0.844700   
598  expl0598  0.6  1.2  1  4  0.7  0.821299            0.842910   
599  expl0599  0.6  1.2  1  4  0.8  0.791608            0.824738   

     Ann_Avg_CVPSWPTotDel_TAF  Std_Ann_Avg_CVPSWPTotDel_TAF  ...  \
0                 8265.886088                    459.372816  ...   
1                 8486.134966                    472.209085  ...   
2                 8140.591856                    464.263070  ...   
3                 7517.455768                    433.720363  ...   
4                 6905.624174                    400.843734  ...   
..                        ...                           ...  ...   
595                       NaN                    331.173458  ...   
596                       NaN                    332.329449  ...   
597                       NaN                    332.492854  ...   
598                       NaN                    331.958025  ...   
599                       NaN                    322.673687  ...   

     Ann_Prob_CVPAGSgtBL90  Ann_Prob_CVPRFSgtBL90  Oct_StDev_X2  Apr_StDev_X2  \
0                 8.536585               0.000000      6.542445     10.346875   
1                15.853659               0.000000      6.414817     10.206163   
2                 7.317073               0.000000      5.933861      9.572897   
3                 1.219512               0.000000      5.909413      9.231497   
4                 0.000000               0.000000      5.926163      8.921624   
..                     ...                    ...           ...           ...   
595               0.000000              64.634146      8.176955     10.292074   
596               0.000000              65.853659      7.965440      9.747449   
597               0.000000              65.853659      5.983565      9.091666   
598               0.000000              65.853659      5.058976      8.797966   
599               0.000000              65.853659      4.241868      8.375252   

     All_Prob_SHSTAflood  Sep_Prob_SHSTAdead  Sep_Prob_OROVLdead  \
0              31.707317            0.000000            0.000000   
1              30.284553            0.000000            0.000000   
2               8.943089            1.219512            1.219512   
3               0.711382            6.097561            4.878049   
4               0.000000           28.048780           13.414634   
..                   ...                 ...                 ...   
595            53.861789            0.000000            0.000000   
596            58.434959            0.000000            0.000000   
597            41.869919            0.000000            0.000000   
598            24.085366            0.000000            0.000000   
599             4.674797            0.000000            0.000000   

     Sep_Prob_TRNTYdead  Sep_Prob_MELONdead  Sep_Prob_MLRTNdead  
0              0.000000            2.439024            0.000000  
1              0.000000            8.536585           78.048780  
2              1.219512           34.146341           85.365854  
3              7.317073           37.804878           84.146341  
4             28.048780           45.121951           82.926829  
..                  ...                 ...                 ...  
595            0.000000            0.000000            0.000000  
596            0.000000            0.000000           68

##### Wet Results

In [282]:
wet_non_sd_metrics = pd.concat([knobs_params_equity_unique_wet_dry, Wet_Ann_Avg_CVPSWPTotDel_TAF_df, Wet_Ann_Avg_SWPTotDel_TAF_df, Wet_Ann_Avg_CVPSCEXDel_TAF_df, Wet_Ann_Avg_SWPMIDel_TAF_df, Wet_Ann_Avg_CVPRefDel_TAF_df, Wet_Ann_Avg_SWPAGDel_TAF_df, Wet_Sep_Avg_NODstorage_TAF_df, Wet_Apr_Avg_NODstorage_TAF_df, Wet_Apr_Avg_ShstaStorage_TAF_df, Wet_Apr_Avg_OrovlStorage_TAF_df, Wet_Ann_Avg_NDO_TAF_df, Wet_Fall_Avg_X2_KM_df, Wet_Spring_Avg_X2_KM_df, Wet_Ann_Avg_CVPTotDel_TAF_df, Wet_Ann_Avg_CVPAgDel_TAF_df, Wet_Ann_Avg_BanksJones_TAF_df, Wet_Ann_Prob_CVPMINgtBL90, Wet_Ann_Prob_CVPMISgtBL90, Wet_Apr_Prob_SHSTAgt38, Wet_Ann_Prob_CVPSCgtBL90, Wet_Ann_Prob_CVPAGNgtBL90, Wet_Ann_Prob_CVPAGSgtBL90, Wet_Ann_Prob_CVPRFSgtBL90, Wet_Oct_StDev_X2, Wet_Apr_StDev_X2, Wet_All_Prob_SHSTAflood, Wet_Sep_Prob_SHSTAdead, Wet_Sep_Prob_OROVLdead, Wet_Sep_Prob_TRNTYdead, Wet_Sep_Prob_MELONdead, Wet_Sep_Prob_MLRTNdead], axis = 1)
wet_non_sd_metrics

Study    d    c  p  r    m  Wet_Ann_Avg_CVPSWPTotDel_TAF  \
0    expl0000  1.0  1.0  0  1  0.0                   7134.695122   
1    expl0001  1.0  1.0  0  1  0.4                   7309.199094   
2    expl0002  1.0  1.0  0  1  0.6                   7050.292857   
3    expl0003  1.0  1.0  0  1  0.7                   6474.400071   
4    expl0004  1.0  1.0  0  1  0.8                   5873.834295   
..        ...  ...  ... .. ..  ...                           ...   
595  expl0595  0.6  1.2  1  4  0.0                           NaN   
596  expl0596  0.6  1.2  1  4  0.4                           NaN   
597  expl0597  0.6  1.2  1  4  0.6                           NaN   
598  expl0598  0.6  1.2  1  4  0.7                           NaN   
599  expl0599  0.6  1.2  1  4  0.8                           NaN   

     Wet_Ann_Avg_SWPTotDel_TAF  Wet_Ann_Avg_CVPSCEXDel_TAF  \
0                  3077.252636                 1936.515222   
1                  3130.378089                 1936.745023   
2                  3069.072979                 1936.499048   
3                  2982.667284                 1936.587476   
4                  2824.948289                 1927.691025   
..                         ...                         ...   
595                        NaN                         NaN   
596                        NaN                         NaN   
597                        NaN                         NaN   
598                        NaN                         NaN   
599                        NaN                         NaN   

     Wet_Ann_Avg_SWPMIDel_TAF  ...  Wet_Ann_Prob_CVPAGSgtBL90  \
0                 1624.498655  ...                   7.462687   
1                 1663.075013  ...                  17.910448   
2                 1627.949137  ...                   8.955224   
3                 1590.037734  ...                   0.000000   
4                 1506.356995  ...                   0.000000   
..                        ...  ...                        ...   
595                       NaN  ...                   0.000000   
596                       NaN  ...                   0.000000   
597                       NaN  ...                   0.000000   
598                       NaN  ...                   0.000000   
599                       NaN  ...                   0.000000   

     Wet_Ann_Prob_CVPRFSgtBL90  Wet_Oct_StDev_X2  Wet_Apr_StDev_X2  \
0                     0.000000          5.568378          6.840707   
1                     0.000000          5.453050          6.835749   
2                     0.000000          5.063713          6.480162   
3                     0.000000          5.153217          6.082184   
4                     0.000000          5.193537          5.488018   
..                         ...               ...               ...   
595                  55.223881          7.781114          6.404587   
596                  55.223881          7.991051          6.433001   
597                  55.223881          5.958152          6.131643   
598                  55.223881          5.233495          5.467307   
599                  55.223881          4.572587          4.883527   

     Wet_All_Prob_SHSTAflood  Wet_Sep_Prob_SHSTAdead  Wet_Sep_Prob_OROVLdead  \
0                  47.435897                0.000000                     0.0   
1                  44.070513                0.000000                     0.0   
2                  12.980769                0.000000                     0.0   
3                   1.121795                0.000000                     0.0   
4                   0.000000               13.461538                     0.0   
..                       ...                     ...                     ...   
595                72.435897                0.000000                     0.0   
596                71.474359                0.000000                     0.0   
597                50.961538                0.000000                     0.0   
598                28.20

In [283]:
wet_sd_results = pd.concat([Wet_Std_Ann_Avg_CVPSWPTotDel_TAF_df, Wet_Std_Ann_Avg_SWPTotDel_TAF_df, Wet_Std_Ann_Avg_CVPSCEXDel_TAF_df, Wet_Std_Ann_Avg_SWPMIDel_TAF_df, Wet_Std_Ann_Avg_CVPRefDel_TAF_df, Wet_Std_Ann_Avg_SWPAGDel_TAF_df, Wet_Std_Sep_Avg_NODstorage_TAF_df, Wet_Std_Apr_Avg_NODstorage_TAF_df, Wet_Std_Apr_Avg_ShstaStorage_TAF_df, Wet_Std_Apr_Avg_OrovlStorage_TAF_df, Wet_Std_Ann_Avg_NDO_TAF_df, Wet_Std_Fall_Avg_X2_KM_df, Wet_Std_Spring_Avg_X2_KM_df, Wet_Std_Ann_Avg_CVPTotDel_TAF_df, Wet_Std_Ann_Avg_CVPAgDel_TAF_df, Wet_Std_Ann_Avg_BanksJones_TAF_df], axis = 1)
wet_sd_results

Wet_Std_Ann_Avg_CVPSWPTotDel_TAF  Wet_Std_Ann_Avg_SWPTotDel_TAF  \
0                          485.912500                     180.090763   
1                          497.067823                     183.519740   
2                          488.264418                     188.331137   
3                          457.234739                     191.557913   
4                          420.652066                     189.916837   
..                                ...                            ...   
595                        338.989289                     164.289427   
596                        340.133439                     165.378850   
597                        341.555390                     167.514100   
598                        341.825199                     168.877826   
599                        333.863510                     163.901255   

     Wet_Std_Ann_Avg_CVPSCEXDel_TAF  Wet_Std_Ann_Avg_SWPMIDel_TAF  \
0                        192.885856                     84.778508   
1                        192.878414                     86.624698   
2                        192.895351                     91.012934   
3                        192.889679                     94.388321   
4                        192.429903                     92.369096   
..                              ...                           ...   
595                      115.872673                     88.995360   
596                      115.702309                     89.754409   
597                      116.084558                     91.931084   
598                      115.879897                     93.434899   
599                             NaN                     91.170156   

     Wet_Std_Ann_Avg_CVPRefDel_TAF  Wet_Std_Sep_Ann_Avg_SWPAGDel_TAF  \
0                        23.615075                        104.263269   
1                        23.647903                        105.400942   
2                        23.676584                        106.511520   
3                        23.675000                        108.082328   
4                        23.624320                        108.716105   
..                             ...                               ...   
595                      23.072901                         78.034548   
596                      23.100861                         78.320856   
597                      23.203458                         78.385141   
598                      23.227420                         78.560376   
599                            NaN                         76.858875   

     Wet_Std_Sep_Avg_NODstorage_TAF  Wet_Std_Apr_Avg_NODstorage_TAF  \
0                       1076.394976                      696.272150   
1                        940.708336                      730.192853   
2                       1157.181638                     1233.958051   
3                       1334.320403                     1351.195128   
4                       1328.209609                     1420.267910   
..                              ...                             ...   
595                      412.852431                      302.807772   
596                      472.107683                      353.967375   
597                      809.376270                      777.219583   
598                      907.039066                      916.494531   
599                     1103.758469                     1032.188976   

     Wet_Std_Apr_Avg_ShstaStorage_TAF  Wet_Std_Apr_Avg_OrovlStorage_TAF  \
0                          248.410736                        301.991662   
1                          277.181016                        423.195822   
2                          799.475061                        691.969721   
3                          777.246085                        825.157490   
4                          586.000911                        854.930513   
..                                ...                               ...   
595                        157.961390                        115.136

In [284]:
wet_results_df = pd.concat([knobs_params_equity_unique_wet_dry, Wet_Ann_Avg_CVPSWPTotDel_TAF_df, Wet_Std_Ann_Avg_CVPSWPTotDel_TAF_df, Wet_Ann_Avg_SWPTotDel_TAF_df, Wet_Std_Ann_Avg_SWPTotDel_TAF_df, Wet_Ann_Avg_CVPSCEXDel_TAF_df, Wet_Std_Ann_Avg_CVPSCEXDel_TAF_df, Wet_Ann_Avg_SWPMIDel_TAF_df, Wet_Std_Ann_Avg_SWPMIDel_TAF_df, Wet_Ann_Avg_CVPRefDel_TAF_df, Wet_Std_Ann_Avg_CVPRefDel_TAF_df, Wet_Ann_Avg_SWPAGDel_TAF_df, Wet_Std_Ann_Avg_SWPAGDel_TAF_df, Wet_Sep_Avg_NODstorage_TAF_df, Wet_Std_Sep_Avg_NODstorage_TAF_df, Wet_Apr_Avg_NODstorage_TAF_df, Wet_Std_Apr_Avg_NODstorage_TAF_df, Wet_Apr_Avg_ShstaStorage_TAF_df, Wet_Std_Apr_Avg_ShstaStorage_TAF_df, Wet_Apr_Avg_OrovlStorage_TAF_df, Wet_Std_Apr_Avg_OrovlStorage_TAF_df, Wet_Ann_Avg_NDO_TAF_df, Wet_Std_Ann_Avg_NDO_TAF_df, Wet_Fall_Avg_X2_KM_df, Wet_Std_Fall_Avg_X2_KM_df, Wet_Spring_Avg_X2_KM_df, Wet_Std_Spring_Avg_X2_KM_df, Wet_Ann_Avg_CVPTotDel_TAF_df, Wet_Std_Ann_Avg_CVPTotDel_TAF_df, Wet_Ann_Avg_CVPAgDel_TAF_df, Wet_Std_Ann_Avg_CVPAgDel_TAF_df, Wet_Ann_Avg_BanksJones_TAF_df, Wet_Std_Ann_Avg_BanksJones_TAF_df, Wet_Ann_Prob_CVPMINgtBL90, Wet_Ann_Prob_CVPMISgtBL90, Wet_Apr_Prob_SHSTAgt38, Wet_Ann_Prob_CVPSCgtBL90, Wet_Ann_Prob_CVPAGNgtBL90, Wet_Ann_Prob_CVPAGSgtBL90, Wet_Ann_Prob_CVPRFSgtBL90, Wet_Oct_StDev_X2, Wet_Apr_StDev_X2, Wet_All_Prob_SHSTAflood, Wet_Sep_Prob_SHSTAdead, Wet_Sep_Prob_OROVLdead, Wet_Sep_Prob_TRNTYdead, Wet_Sep_Prob_MELONdead, Wet_Sep_Prob_MLRTNdead], axis=1)
wet_results_df

Study    d    c  p  r    m  Wet_Ann_Avg_CVPSWPTotDel_TAF  \
0    expl0000  1.0  1.0  0  1  0.0                   7134.695122   
1    expl0001  1.0  1.0  0  1  0.4                   7309.199094   
2    expl0002  1.0  1.0  0  1  0.6                   7050.292857   
3    expl0003  1.0  1.0  0  1  0.7                   6474.400071   
4    expl0004  1.0  1.0  0  1  0.8                   5873.834295   
..        ...  ...  ... .. ..  ...                           ...   
595  expl0595  0.6  1.2  1  4  0.0                           NaN   
596  expl0596  0.6  1.2  1  4  0.4                           NaN   
597  expl0597  0.6  1.2  1  4  0.6                           NaN   
598  expl0598  0.6  1.2  1  4  0.7                           NaN   
599  expl0599  0.6  1.2  1  4  0.8                           NaN   

     Wet_Std_Ann_Avg_CVPSWPTotDel_TAF  Wet_Ann_Avg_SWPTotDel_TAF  \
0                          485.912500                3077.252636   
1                          497.067823                3130.378089   
2                          488.264418                3069.072979   
3                          457.234739                2982.667284   
4                          420.652066                2824.948289   
..                                ...                        ...   
595                        338.989289                        NaN   
596                        340.133439                        NaN   
597                        341.555390                        NaN   
598                        341.825199                        NaN   
599                        333.863510                        NaN   

     Wet_Std_Ann_Avg_SWPTotDel_TAF  ...  Wet_Ann_Prob_CVPAGSgtBL90  \
0                       180.090763  ...                   7.462687   
1                       183.519740  ...                  17.910448   
2                       188.331137  ...                   8.955224   
3                       191.557913  ...                   0.000000   
4                       189.916837  ...                   0.000000   
..                             ...  ...                        ...   
595                     164.289427  ...                   0.000000   
596                     165.378850  ...                   0.000000   
597                     167.514100  ...                   0.000000   
598                     168.877826  ...                   0.000000   
599                     163.901255  ...                   0.000000   

     Wet_Ann_Prob_CVPRFSgtBL90  Wet_Oct_StDev_X2  Wet_Apr_StDev_X2  \
0                     0.000000          5.568378          6.840707   
1                     0.000000          5.453050          6.835749   
2                     0.000000          5.063713          6.480162   
3                     0.000000          5.153217          6.082184   
4                     0.000000          5.193537          5.488018   
..                         ...               ...               ...   
595                  55.223881          7.781114          6.404587   
596                  55.223881          7.991051          6.433001   
597                  55.223881          5.958152          6.131643   
598                  55.223881          5.233495          5.467307   
599                  55.223881          4.572587          4.883527   

     Wet_All_Prob_SHSTAflood  Wet_Sep_Prob_SHSTAdead  Wet_Sep_Prob_OROVLdead  \
0                  47.435897                0.000000                     0.0   
1                  44.070513                0.000000                     0.0   
2                  12.980769                0.000000                     0.0   
3                   1.121795                0.000000                     0.0   
4                   0.000000               13.461538                     0.0   
..                       ...                     ...                     ...   
595                72.435897                0.000000                     0.0   
596                71.474359                0.000000

##### Dry Results

In [285]:
dry_non_sd_metrics = pd.concat([knobs_params_equity_unique_wet_dry, Dry_Ann_Avg_CVPSWPTotDel_TAF_df, Dry_Ann_Avg_SWPTotDel_TAF_df, Dry_Ann_Avg_CVPSCEXDel_TAF_df, Dry_Ann_Avg_SWPMIDel_TAF_df, Dry_Ann_Avg_CVPRefDel_TAF_df, Dry_Ann_Avg_SWPAGDel_TAF_df, Dry_Sep_Avg_NODstorage_TAF_df, Dry_Apr_Avg_NODstorage_TAF_df, Dry_Apr_Avg_ShstaStorage_TAF_df, Dry_Apr_Avg_OrovlStorage_TAF_df, Dry_Ann_Avg_NDO_TAF_df, Dry_Fall_Avg_X2_KM_df, Dry_Spring_Avg_X2_KM_df, Dry_Ann_Avg_CVPTotDel_TAF_df, Dry_Ann_Avg_CVPAgDel_TAF_df, Dry_Ann_Avg_BanksJones_TAF_df, Dry_Ann_Prob_CVPMINgtBL90, Dry_Ann_Prob_CVPMISgtBL90, Dry_Apr_Prob_SHSTAgt38, Dry_Ann_Prob_CVPSCgtBL90, Dry_Ann_Prob_CVPAGNgtBL90, Dry_Ann_Prob_CVPAGSgtBL90, Dry_Ann_Prob_CVPRFSgtBL90, Dry_Oct_StDev_X2, Dry_Apr_StDev_X2, Dry_All_Prob_SHSTAflood, Dry_Sep_Prob_SHSTAdead, Dry_Sep_Prob_OROVLdead, Dry_Sep_Prob_TRNTYdead, Dry_Sep_Prob_MELONdead,Dry_Sep_Prob_MLRTNdead], axis = 1)
dry_non_sd_metrics

Study    d    c  p  r    m  Dry_Ann_Avg_CVPSWPTotDel_TAF  \
0    expl0000  1.0  1.0  0  1  0.0                   4439.513024   
1    expl0001  1.0  1.0  0  1  0.4                   4581.038398   
2    expl0002  1.0  1.0  0  1  0.6                   4336.864684   
3    expl0003  1.0  1.0  0  1  0.7                   4058.812627   
4    expl0004  1.0  1.0  0  1  0.8                   3838.095211   
..        ...  ...  ... .. ..  ...                           ...   
595  expl0595  0.6  1.2  1  4  0.0                           NaN   
596  expl0596  0.6  1.2  1  4  0.4                           NaN   
597  expl0597  0.6  1.2  1  4  0.6                           NaN   
598  expl0598  0.6  1.2  1  4  0.7                           NaN   
599  expl0599  0.6  1.2  1  4  0.8                           NaN   

     Dry_Ann_Avg_SWPTotDel_TAF  Dry_Ann_Avg_CVPSCEXDel_TAF  \
0                  1706.727740                 1598.151569   
1                  1716.369619                 1598.399219   
2                  1577.817420                 1595.301621   
3                  1577.374411                 1566.862872   
4                  1570.570845                 1487.607434   
..                         ...                         ...   
595                        NaN                         NaN   
596                        NaN                         NaN   
597                        NaN                         NaN   
598                        NaN                         NaN   
599                        NaN                         NaN   

     Dry_Ann_Avg_SWPMIDel_TAF  ...  Dry_Ann_Prob_CVPAGSgtBL90  \
0                  784.747989  ...                   6.666667   
1                  802.235657  ...                  22.222222   
2                  755.433952  ...                  15.555556   
3                  787.512231  ...                   2.222222   
4                  816.360449  ...                   0.000000   
..                        ...  ...                        ...   
595                       NaN  ...                  15.555556   
596                       NaN  ...                  15.555556   
597                       NaN  ...                  15.555556   
598                       NaN  ...                  15.555556   
599                       NaN  ...                  13.333333   

     Dry_Ann_Prob_CVPRFSgtBL90  Dry_Oct_StDev_X2  Dry_Apr_StDev_X2  \
0                     0.000000          0.864057          7.934651   
1                     0.000000          1.059890          8.220776   
2                     0.000000          1.091209          8.138063   
3                     0.000000          1.000563          8.131305   
4                     0.000000          1.209964          8.273841   
..                         ...               ...               ...   
595                   2.222222          3.561314          9.136112   
596                   2.222222          3.642758          8.694704   
597                   2.222222          3.373395          8.241827   
598                   2.222222          2.597599          8.404734   
599                   2.222222          2.005620          8.402864   

     Dry_All_Prob_SHSTAflood  Dry_Sep_Prob_SHSTAdead  Dry_Sep_Prob_OROVLdead  \
0                   4.444444                0.000000                0.000000   
1                   6.388889                0.000000                0.000000   
2                   1.944444                3.333333                3.333333   
3                   0.000000               16.666667               13.333333   
4                   0.000000               53.333333               36.666667   
..                       ...                     ...                     ...   
595                21.666667                0.000000                0.000000   
596                35.833333                0.000000                0.000000   
597                26.111111                0.000000                0.000000   
598                16.94

In [286]:
dry_sd_results = pd.concat([Dry_Std_Ann_Avg_CVPSWPTotDel_TAF_df, Dry_Std_Ann_Avg_SWPTotDel_TAF_df, Dry_Std_Ann_Avg_CVPSCEXDel_TAF_df, Dry_Std_Ann_Avg_SWPMIDel_TAF_df, Dry_Std_Ann_Avg_CVPRefDel_TAF_df, Dry_Std_Ann_Avg_SWPAGDel_TAF_df, Dry_Std_Sep_Avg_NODstorage_TAF_df, Dry_Std_Apr_Avg_NODstorage_TAF_df, Dry_Std_Apr_Avg_ShstaStorage_TAF_df, Dry_Std_Apr_Avg_OrovlStorage_TAF_df, Dry_Std_Ann_Avg_NDO_TAF_df, Dry_Std_Fall_Avg_X2_KM_df, Dry_Std_Spring_Avg_X2_KM_df, Dry_Std_Ann_Avg_CVPTotDel_TAF_df, Dry_Std_Ann_Avg_CVPAgDel_TAF_df, Dry_Std_Ann_Avg_BanksJones_TAF_df], axis = 1)
dry_sd_results

Dry_Std_Ann_Avg_CVPSWPTotDel_TAF  Dry_Std_Ann_Avg_SWPTotDel_TAF  \
0                          373.804162                     142.179663   
1                          391.358897                     142.215862   
2                          383.536557                     136.064858   
3                          360.345613                     135.579672   
4                          344.092879                     133.386299   
..                                ...                            ...   
595                        312.336140                     147.641032   
596                        313.642592                     149.523962   
597                        308.478179                     142.652016   
598                        302.172627                     131.897049   
599                        289.880241                     121.812525   

     Dry_Std_Ann_Avg_CVPSCEXDel_TAF  Dry_Std_Ann_Avg_SWPMIDel_TAF  \
0                        182.958329                     66.741903   
1                        182.941835                     65.373479   
2                        182.844539                     58.918440   
3                        181.990108                     58.560798   
4                        178.743126                     57.985077   
..                              ...                           ...   
595                      111.743082                     82.036424   
596                      112.118809                     83.979093   
597                      111.916653                     78.773887   
598                      111.179248                     71.420321   
599                             NaN                     64.240514   

     Dry_Std_Ann_Avg_CVPRefDel_TAF  Dry_Std_Sep_Ann_Avg_SWPAGDel_TAF  \
0                        22.206716                         85.716054   
1                        22.163040                         87.611161   
2                        22.203968                         89.247799   
3                        22.079108                         90.047536   
4                        21.346609                         88.216305   
..                             ...                               ...   
595                      22.507644                         68.905617   
596                      22.493984                         69.087271   
597                      22.735907                         67.648085   
598                      22.149018                         65.170309   
599                            NaN                         63.053042   

     Dry_Std_Sep_Avg_NODstorage_TAF  Dry_Std_Apr_Avg_NODstorage_TAF  \
0                       1310.736814                     1640.807625   
1                       1299.638337                     1526.906957   
2                       1480.269723                     1706.187301   
3                       1238.639036                     1560.863664   
4                        628.369324                     1102.797508   
..                              ...                             ...   
595                     1023.075609                     1273.591393   
596                      781.197028                     1132.172760   
597                      826.618772                     1234.151156   
598                      841.954019                     1148.853454   
599                      716.625450                      879.771368   

     Dry_Std_Apr_Avg_ShstaStorage_TAF  Dry_Std_Apr_Avg_OrovlStorage_TAF  \
0                          756.807174                        496.137603   
1                          636.778066                        515.071978   
2                          846.490160                        488.939535   
3                          794.185489                        513.323966   
4                          553.071648                        452.793603   
..                                ...                               ...   
595                        423.716044                        543.949

In [287]:
dry_results_df = pd.concat([knobs_params_equity_unique_wet_dry, Dry_Ann_Avg_CVPSWPTotDel_TAF_df, Dry_Std_Ann_Avg_CVPSWPTotDel_TAF_df, Dry_Ann_Avg_SWPTotDel_TAF_df, Dry_Std_Ann_Avg_SWPTotDel_TAF_df, Dry_Ann_Avg_CVPSCEXDel_TAF_df, Dry_Std_Ann_Avg_CVPSCEXDel_TAF_df, Dry_Ann_Avg_SWPMIDel_TAF_df, Dry_Std_Ann_Avg_SWPMIDel_TAF_df, Dry_Ann_Avg_CVPRefDel_TAF_df, Dry_Std_Ann_Avg_CVPRefDel_TAF_df, Dry_Ann_Avg_SWPAGDel_TAF_df, Dry_Std_Ann_Avg_SWPAGDel_TAF_df, Dry_Sep_Avg_NODstorage_TAF_df, Dry_Std_Sep_Avg_NODstorage_TAF_df, Dry_Apr_Avg_NODstorage_TAF_df, Dry_Std_Apr_Avg_NODstorage_TAF_df, Dry_Apr_Avg_ShstaStorage_TAF_df, Dry_Std_Apr_Avg_ShstaStorage_TAF_df, Dry_Apr_Avg_OrovlStorage_TAF_df, Dry_Std_Apr_Avg_OrovlStorage_TAF_df, Dry_Ann_Avg_NDO_TAF_df, Dry_Std_Ann_Avg_NDO_TAF_df, Dry_Fall_Avg_X2_KM_df, Dry_Std_Fall_Avg_X2_KM_df, Dry_Spring_Avg_X2_KM_df, Dry_Std_Spring_Avg_X2_KM_df, Dry_Ann_Avg_CVPTotDel_TAF_df, Dry_Std_Ann_Avg_CVPTotDel_TAF_df, Dry_Ann_Avg_CVPAgDel_TAF_df, Dry_Std_Ann_Avg_CVPAgDel_TAF_df, Dry_Ann_Avg_BanksJones_TAF_df, Dry_Std_Ann_Avg_BanksJones_TAF_df, Dry_Ann_Prob_CVPMINgtBL90, Dry_Ann_Prob_CVPMISgtBL90, Dry_Apr_Prob_SHSTAgt38, Dry_Ann_Prob_CVPSCgtBL90, Dry_Ann_Prob_CVPAGNgtBL90, Dry_Ann_Prob_CVPAGSgtBL90, Dry_Ann_Prob_CVPRFSgtBL90, Dry_Oct_StDev_X2, Dry_Apr_StDev_X2, Dry_All_Prob_SHSTAflood, Dry_Sep_Prob_SHSTAdead, Dry_Sep_Prob_OROVLdead, Dry_Sep_Prob_TRNTYdead, Dry_Sep_Prob_MELONdead, Dry_Sep_Prob_MLRTNdead], axis=1)
dry_results_df

Study    d    c  p  r    m  Dry_Ann_Avg_CVPSWPTotDel_TAF  \
0    expl0000  1.0  1.0  0  1  0.0                   4439.513024   
1    expl0001  1.0  1.0  0  1  0.4                   4581.038398   
2    expl0002  1.0  1.0  0  1  0.6                   4336.864684   
3    expl0003  1.0  1.0  0  1  0.7                   4058.812627   
4    expl0004  1.0  1.0  0  1  0.8                   3838.095211   
..        ...  ...  ... .. ..  ...                           ...   
595  expl0595  0.6  1.2  1  4  0.0                           NaN   
596  expl0596  0.6  1.2  1  4  0.4                           NaN   
597  expl0597  0.6  1.2  1  4  0.6                           NaN   
598  expl0598  0.6  1.2  1  4  0.7                           NaN   
599  expl0599  0.6  1.2  1  4  0.8                           NaN   

     Dry_Std_Ann_Avg_CVPSWPTotDel_TAF  Dry_Ann_Avg_SWPTotDel_TAF  \
0                          373.804162                1706.727740   
1                          391.358897                1716.369619   
2                          383.536557                1577.817420   
3                          360.345613                1577.374411   
4                          344.092879                1570.570845   
..                                ...                        ...   
595                        312.336140                        NaN   
596                        313.642592                        NaN   
597                        308.478179                        NaN   
598                        302.172627                        NaN   
599                        289.880241                        NaN   

     Dry_Std_Ann_Avg_SWPTotDel_TAF  ...  Dry_Ann_Prob_CVPAGSgtBL90  \
0                       142.179663  ...                   6.666667   
1                       142.215862  ...                  22.222222   
2                       136.064858  ...                  15.555556   
3                       135.579672  ...                   2.222222   
4                       133.386299  ...                   0.000000   
..                             ...  ...                        ...   
595                     147.641032  ...                  15.555556   
596                     149.523962  ...                  15.555556   
597                     142.652016  ...                  15.555556   
598                     131.897049  ...                  15.555556   
599                     121.812525  ...                  13.333333   

     Dry_Ann_Prob_CVPRFSgtBL90  Dry_Oct_StDev_X2  Dry_Apr_StDev_X2  \
0                     0.000000          0.864057          7.934651   
1                     0.000000          1.059890          8.220776   
2                     0.000000          1.091209          8.138063   
3                     0.000000          1.000563          8.131305   
4                     0.000000          1.209964          8.273841   
..                         ...               ...               ...   
595                   2.222222          3.561314          9.136112   
596                   2.222222          3.642758          8.694704   
597                   2.222222          3.373395          8.241827   
598                   2.222222          2.597599          8.404734   
599                   2.222222          2.005620          8.402864   

     Dry_All_Prob_SHSTAflood  Dry_Sep_Prob_SHSTAdead  Dry_Sep_Prob_OROVLdead  \
0                   4.444444                0.000000                0.000000   
1                   6.388889                0.000000                0.000000   
2                   1.944444                3.333333                3.333333   
3                   0.000000               16.666667               13.333333   
4                   0.000000               53.333333               36.666667   
..                       ...                     ...                     ...   
595                21.666667                0.000000                0.000000   
596                35.833333                0.000000

#### Write to csv

In [295]:
all_results_df.to_csv(os.path.join(fPath, MetricsOut))
all_results_df[metrics_output].to_csv(os.path.join(fPath, "filtered_" + MetricsOut))

In [296]:
wet_results_df.to_csv(os.path.join(fPath, WetMetricsOut))
wet_results_df[wet_metrics_output].to_csv(os.path.join(fPath, "filtered_" + WetMetricsOut))
dry_results_df.to_csv(os.path.join(fPath, DryMetricsOut))
dry_results_df[dry_metrics_output].to_csv(os.path.join(fPath, "filtered_" + DryMetricsOut))

In [297]:
all_sd_results.to_csv(os.path.join(fPath, MetricsSdOut))
all_sd_results[metrics_sd_output].to_csv(os.path.join(fPath, "filtered_" + MetricsSdOut))

In [298]:
wet_sd_results.to_csv(os.path.join(fPath, WetMetricsSdOut))
wet_sd_results[wet_metrics_sd_output].to_csv(os.path.join(fPath, "filtered_" + WetMetricsSdOut))

In [299]:
dry_sd_results.to_csv(os.path.join(fPath, DryMetricsSdOut))
dry_sd_results[dry_metrics_sd_output].to_csv(os.path.join(fPath, "filtered_" + DryMetricsSdOut))

##### UNUSED EXCEEDANCE FUNCTION CODE

In [ ]:
# 
# Point out this may not be working as intended - I used this one when I was receiving exceedance < 0.9 for all values.
# def calculate_exceedance_probabilities(data):
#     # Initialize an empty dataframe to store results
#     exceedance_probs = pd.DataFrame(np.nan, index=range(len(data)), columns=data.columns)
# 
#     # Loop through each column
#     for col in data.columns:
#         # Sort the column in descending order
#         sorted_col = data[col].sort_values(ascending=False)
# 
#         #Calculate exceedance probabilities for each ranked flow value
#         exceedance_prob = [(sorted_col > value).mean() for value in sorted_col]
# 
#         # Store the result in the dataframe
#         exceedance_probs[col] = exceedance_prob
# 
#     return exceedance_probs

# from statsmodels.distributions.empirical_distribution import ECDF
# 
# def calculate_exceedance_probabilities(df):
#     exceedance_df = pd.DataFrame(index=df.index)
# 
#     for column in df.columns:
#         ecdf = ECDF(df[column])
#         exceedance_probs = 1 - ecdf(df[column])
#         exceedance_df[column] = exceedance_probs
# 
#     return exceedance_df